# Binance Cryptocurrency Pair Analysis: Data-Driven

# 1. Introduction

This analysis focuses on the trading activity of various cryptocurrency pairs involving fiat currencies on Binance. We begin by retrieving data through the Binance API, filtering for relevant pairs, and analyzing trading volumes in USD, particularly for key cryptocurrencies like BTC, ETH, and USDT. The aim is to uncover insights into trading patterns and market behavior on the Binance platform.

In this notebook, we conduct a comprehensive evaluation of currency pairs that involve fiat currencies. We will also identify any new fiat currencies recently added to the platform, offering a data-driven perspective on the dynamics of fiat-crypto exchanges on Binance.

*For a more general overview and the key takeaways from this analysis, you can read my [LinkedIn article](https://www.linkedin.com/in/tu-perfil/) on the topic.*


## 1.1 Loading Necessary Libraries
In this section, we will import the essential libraries required for retrieving data from the Binance API, organizing it for analysis, and managing file storage. The libraries serve the following purposes:

- requests: To make HTTP requests and retrieve data from the Binance API.
- pandas: To manipulate and structure the data into DataFrames, allowing for easier analysis.
- os: To manage file directories and ensure that data can be saved and accessed efficiently throughout the process.

In [1]:
import requests  # To handle HTTP requests to the Binance API
import pandas as pd  # To structure and manipulate the data obtained
import os  # To manage directories for saving the data

## 1.2 Setting Up Directories**
We will set up a base directory to store the data files downloaded from Binance. This ensures that all data is organized and easily accessible for further analysis.

In [2]:
# Definir la carpeta base donde se guardarán los archivos CSV
base_folder = 'datos_historicos_binance'

# Crear la carpeta base si no existe
if not os.path.exists(base_folder):
    os.makedirs(base_folder)

# 2. Data Retrieval and Download

## 2.1 Retrieving Information on Currency Pairs in Binance

In this section, we will retrieve information on all available currency pairs on Binance using their API. Our goal is to identify pairs that involve fiat currencies, as these will be the focus of our analysis.

We will use the following list of fiat currencies, grouped into Advanced Economies (AEs) and Emerging Market and Developing Economies (EMDEs).

In [6]:
# Lista completa de monedas fiat
fiat_currencies = [
    'USD', 'EUR', 'GBP', 'JPY', 'AUD', 'CAD', 'CHF', 'CNY', 'INR', 'RUB', 
    'BRL', 'ARS', 'NGN', 'TRY', 'MXN', 'ZAR', 'PLN', 'SEK', 'NOK', 'DKK', 
    'HKD', 'SGD', 'NZD', 'KRW', 'THB', 'MYR', 'IDR', 'PHP', 'VND', 'CZK', 
    'HUF', 'RON', 'BGN', 'HRK', 'RSD', 'UAH', 'KZT', 'AZN', 'GEL', 'BYN',
    'EGP', 'ILS', 'SAR', 'AED', 'QAR', 'KWD', 'BHD', 'OMR', 'TND', 'MAD', 
    'DZD', 'TWD', 'LKR', 'PKR', 'BDT', 'KES', 'TZS', 'UGX', 'GHS', 'XAF', 
    'XOF', 'XPF', 'MUR', 'SCR', 'MGA', 'ZMW', 'MWK', 'BWP', 'NAD', 'SLL',
    'LRD', 'LSL', 'SZL', 'MZN', 'BIF', 'CDF', 'DJF', 'ETB', 'GNF', 'HTG',
    'LRD', 'MGA', 'NPR', 'PGK', 'PGK', 'SHP', 'SLL', 'SOS', 'SSP', 'STD',
    'SYP', 'TOP', 'TTD', 'TWD', 'VUV', 'WST', 'XCD', 'YER', 'ZMW'
]

In [7]:
def obtener_info_pares_binance():
    # URL del endpoint de exchangeInfo de Binance
    url = 'https://api.binance.com/api/v3/exchangeInfo'
    
    # Realizar la solicitud GET al endpoint
    response = requests.get(url)
    
    # Verificar si la solicitud fue exitosa
    if response.status_code == 200:
        # Convertir los datos de respuesta a formato JSON
        data = response.json()
        
        # Crear un diccionario para almacenar la información sobre los pares de divisas
        info_pares = {}
        
        # Iterar sobre los datos para obtener la información relevante sobre cada par de divisas
        for symbol_info in data['symbols']:
            symbol = symbol_info['symbol']
            base_currency = symbol_info['baseAsset']
            quote_currency = symbol_info['quoteAsset']
            
            # Almacenar la información en el diccionario
            info_pares[symbol] = {'base_currency': base_currency, 'quote_currency': quote_currency}
        
        return info_pares
    else:
        print(f"Error al obtener información sobre los pares de divisas de Binance. Código de estado: {response.status_code}")
        return None

# Obtener información sobre los pares de divisas
info_pares = obtener_info_pares_binance()

## Visualizing the Network of Currency Pairs
Next, we create a network graph to visualize the relationships between fiat currencies and cryptocurrencies based on Binance trading pairs. We will focus on AEs and EMDEs to highlight their interactions.

In [10]:
import igraph as ig
import plotly.graph_objects as go

# Suponiendo que 'info_pares' contiene el diccionario con la información de los pares de divisas
info_pares = obtener_info_pares_binance()

# Listas de monedas fiat para AEs y EMDEs
aes_fiat_currencies = ['USD', 'EUR', 'GBP', 'JPY', 'AUD', 'CAD', 'CHF', 'CZK']
emdes_fiat_currencies = [
    'BRL', 'ARS', 'NGN', 'TRY', 'MXN', 'ZAR', 'PLN', 'RUB', 'RON', 'UAH'
]

# Colores
aes_color = '#AA322F'  # Rojo oscuro para AEs
emdes_color = '#6FA5E2'  # Azul pastel más oscuro para EMDEs
crypto_color = '#D3D3D3'  # Gris claro para criptomonedas
crypto_label_color = '#A9A9A9'  # Gris un poco más oscuro para etiquetas de criptomonedas

# Extraer los vertices y las aristas a partir de 'info_pares'
vertices = set()
edges = []

for symbol, details in info_pares.items():
    base_currency = details['base_currency']
    quote_currency = details['quote_currency']
    vertices.add(base_currency)
    vertices.add(quote_currency)
    edges.append((base_currency, quote_currency))

# Convertir el conjunto de vertices a una lista
vertices = list(vertices)

# Crear el grafo en igraph
G_ig = ig.Graph()
G_ig.add_vertices(vertices)
G_ig.add_edges(edges)

# Filtrar nodos con grado menor que 3
low_degree_nodes = [v.index for v in G_ig.vs if G_ig.degree(v) < 3]
G_ig.delete_vertices(low_degree_nodes)

# Recalcular el PageRank después de eliminar los nodos de bajo grado
pagerank = G_ig.pagerank()
max_pagerank = max(pagerank)

# Exagerar las diferencias aplicando una transformación exponencial al PageRank
min_size = 1  # Tamaño mínimo para nodos con solo 3 conexiones
mid_size = 10 # Tamaño para nodos con 4 conexiones
max_size = 40 # Tamaño máximo para nodos con más conexiones y alto PageRank

# Asignar tamaños basados en el número de conexiones y PageRank
vertex_sizes = []
for i in range(len(G_ig.vs)):
    degree = G_ig.degree(i)
    if degree == 3:
        vertex_sizes.append(min_size)
    elif degree == 4:
        vertex_sizes.append(mid_size)
    else:
        vertex_sizes.append(min_size + (pagerank[i] / max_pagerank) ** 0.3 * (max_size - min_size))

# Encontrar las criptomonedas con los 5 mayores valores de PageRank
top_5_cryptos = sorted(range(len(pagerank)), key=lambda i: pagerank[i], reverse=True)[:5]

# Asignar colores a los nodos y etiquetas: AEs, EMDEs y criptomonedas
vertex_colors = []
label_colors = []
for i in range(len(G_ig.vs)):
    if G_ig.vs[i]['name'] in aes_fiat_currencies:
        vertex_colors.append(aes_color)
        label_colors.append(aes_color)
    elif G_ig.vs[i]['name'] in emdes_fiat_currencies:
        vertex_colors.append(emdes_color)
        label_colors.append(emdes_color)
    else:
        vertex_colors.append(crypto_color)
        label_colors.append(crypto_label_color)

# Asignar forma a los nodos
vertex_shapes = [
    'triangle-up' if G_ig.vs[i]['name'] in aes_fiat_currencies or G_ig.vs[i]['name'] in emdes_fiat_currencies else 'circle'
    for i in range(len(G_ig.vs))
]

# Asignar etiquetas a las monedas fiat y a las criptomonedas en el top 5 de PageRank
vertex_labels = [
    G_ig.vs[i]['name'] if G_ig.vs[i]['name'] in aes_fiat_currencies or G_ig.vs[i]['name'] in emdes_fiat_currencies or i in top_5_cryptos else ''
    for i in range(len(G_ig.vs))
]

# Definir tamaños de las etiquetas basados en PageRank
min_font_size = 8
max_font_size = 18
vertex_label_sizes = [min_font_size + (pr / max_pagerank) ** 0.3 * (max_font_size - min_font_size) for pr in pagerank]

# Aplicar el layout de Fruchterman-Reingold
layout = G_ig.layout_fruchterman_reingold()

# Extraer las posiciones del layout y ajustar para aristas curvas
Xn = [layout[k][0] for k in range(len(G_ig.vs))]
Yn = [layout[k][1] for k in range(len(G_ig.vs))]
Xe = []
Ye = []
for edge in G_ig.es:
    x_mid = (layout[edge.source][0] + layout[edge.target][0]) / 2
    y_mid = (layout[edge.source][1] + layout[edge.target][1]) / 2
    Xe += [layout[edge.source][0], x_mid, layout[edge.target][0], None]
    Ye += [layout[edge.source][1], y_mid, layout[edge.target][1], None]

# Graficar usando Plotly
trace1 = go.Scatter(
    x=Xe,
    y=Ye,
    mode='lines',
    line=dict(color='rgb(240, 240, 240)', width=1),  # Líneas de color gris claro
    hoverinfo='none'
)

trace2 = go.Scatter(
    x=Xn,
    y=Yn,
    mode='markers+text',
    name='ntw',
    marker=dict(
        symbol=vertex_shapes,
        size=vertex_sizes, 
        color=vertex_colors,
        line=dict(width=0)  # Eliminar el borde de los nodos
    ),
    text=vertex_labels,
    textposition='top center',
    textfont=dict(color=label_colors, size=vertex_label_sizes),  # Usar tamaños de fuente basados en PageRank
    hoverinfo='text'
)

layout_plot = go.Layout(
    title='<b>Cryptocurrency-Fiat Exchange Network: A Visual Analysis of Market Interactions Across Economies<b>',
    title_font_color="#AA322F",  
    font=dict(size=12),
    showlegend=False,
    autosize=False,
    width=800,
    height=800,
    paper_bgcolor='white',  # Fondo blanco
    plot_bgcolor='white',   # Fondo blanco del área de trazado
    xaxis=dict(showline=False, zeroline=False, showgrid=False, showticklabels=False),
    yaxis=dict(showline=False, zeroline=False, showgrid=False, showticklabels=False),
    margin=dict(l=40, r=40, b=85, t=100),
    hovermode='closest'
)

fig = go.Figure(data=[trace1, trace2], layout=layout_plot)
fig.show()


## 2.2 Filtering Currency Pairs by Fiat Currencies

Once we have retrieved all the currency pair information from Binance, the next step is to filter out pairs that specifically involve fiat currencies. This step allows us to focus the analysis on the most relevant pairs for fiat-to-crypto or fiat-to-fiat exchanges.


In [11]:
# Filter to obtain only the pairs involving fiat currencies
fiat_pairs = [pair for pair, currencies in info_pares.items() if currencies['quote_currency'] in fiat_currencies or currencies['base_currency'] in fiat_currencies]

# Output the total number of pairs involving fiat currencies
print(f"Total pairs with fiat currencies: {len(fiat_pairs)}")

Total pairs with fiat currencies: 462


## 2.3 Downloading and Saving Historical Data for Fiat-Crypto Pairs on Binance

In this section, we will retrieve historical daily trading data for each of the fiat-crypto pairs identified. The data will be fetched from Binance's API and saved as monthly CSV files, organized by fiat and cryptocurrency for easy reference and further analysis.

In [12]:
import requests
import pandas as pd
import os
from tqdm.notebook import tqdm

# Define the base folder where CSV files will be stored
base_folder = 'datos_historicos_binance'

# Create the base folder if it does not exist
if not os.path.exists(base_folder):
    os.makedirs(base_folder)

# Initialize a counter and a list to track saved files
total_files_saved = 0
saved_files = []

def obtener_datos_y_guardar_csv(symbol, base_currency, quote_currency):
    global total_files_saved
    global saved_files

    # Build the URL for the Binance API
    url = f'https://api.binance.com/api/v3/klines?symbol={symbol}&interval=1d'
    
    # Send a GET request to the API
    response = requests.get(url)
    
    # Check if the request was successful
    if response.status_code == 200:
        # Convert the response data to JSON format
        data = response.json()
        
        # Create a pandas DataFrame with the data
        df = pd.DataFrame(data, columns=[
            'timestamp', 'open', 'high', 'low', 'close', 'volume', 
            'close_time', 'quote_asset_volume', 'number_of_trades', 
            'taker_buy_base_asset_volume', 'taker_buy_quote_asset_volume', 'ignore'
        ])
        
        # Convert the 'timestamp' column to datetime format
        df['timestamp'] = pd.to_datetime(df['timestamp'], unit='ms')
        
        # Determine the fiat currency and cryptocurrency based on their position
        if base_currency in fiat_currencies:
            fiat_currency = base_currency
            crypto_currency = quote_currency
        else:
            fiat_currency = quote_currency
            crypto_currency = base_currency
        
        # Create a folder for the fiat currency if it doesn't exist
        fiat_folder_path = os.path.join(base_folder, fiat_currency)
        if not os.path.exists(fiat_folder_path):
            os.makedirs(fiat_folder_path)
        
        # Create a subfolder for the cryptocurrency if it doesn't exist
        crypto_folder_path = os.path.join(fiat_folder_path, crypto_currency)
        if not os.path.exists(crypto_folder_path):
            os.makedirs(crypto_folder_path)
        
        # Save the data into monthly CSV files with daily data inside
        for month, df_month in df.groupby(df['timestamp'].dt.to_period('M')):
            csv_file_path = os.path.join(crypto_folder_path, f'{fiat_currency.lower()}_{crypto_currency.lower()}_{month.start_time.strftime("%Y-%m")}.csv')
            df_month.to_csv(csv_file_path, index=False)
            total_files_saved += 1
            saved_files.append(csv_file_path)
    else:
        print(f"Error fetching data for {symbol}. Status code: {response.status_code}")

# Download data for all the pairs of interest with a progress bar
for pair in tqdm(fiat_pairs, desc="Processing pairs"):
    base_currency = info_pares[pair]['base_currency']
    quote_currency = info_pares[pair]['quote_currency']
    obtener_datos_y_guardar_csv(pair, base_currency, quote_currency)

# Summary message
print(f"Total files saved: {total_files_saved}")


Processing pairs:   0%|          | 0/462 [00:00<?, ?it/s]

Total files saved: 6099


## 2.3 Loading and Combining the Data for Analysis

In this section, we will load the historical data saved in CSV format for each fiat-crypto pair. By combining these individual files into a single DataFrame, we streamline the analysis process, ensuring that all the data is accessible in one place.

In [13]:
import os
import pandas as pd
from tqdm.notebook import tqdm

# Initialize a list to store the DataFrames
dfs = []

# Get the list of fiat currencies to iterate over and initialize the progress bar
fiat_currencies = [f for f in os.listdir(base_folder) if os.path.isdir(os.path.join(base_folder, f))]

# Iterate through the fiat currency folders with a progress bar
for fiat_currency in tqdm(fiat_currencies, desc="Processing fiat currencies"):
    fiat_folder_path = os.path.join(base_folder, fiat_currency)
    
    # Iterate through the cryptocurrency folders within each fiat currency folder
    for crypto_currency in os.listdir(fiat_folder_path):
        crypto_folder_path = os.path.join(fiat_folder_path, crypto_currency)
        if os.path.isdir(crypto_folder_path):
            # Iterate through the CSV files within each cryptocurrency folder
            for csv_file in os.listdir(crypto_folder_path):
                csv_file_path = os.path.join(crypto_folder_path, csv_file)
                if csv_file_path.endswith('.csv'):
                    # Load the CSV into a pandas DataFrame
                    df = pd.read_csv(csv_file_path)
                    # Add columns for the fiat and cryptocurrency labels
                    df['fiat_currency'] = fiat_currency
                    df['crypto_currency'] = crypto_currency
                    # Append the DataFrame to the list
                    dfs.append(df)

# Combine all the DataFrames into one single DataFrame
final_df = pd.concat(dfs, ignore_index=True)

# Display the structure of the final DataFrame
print(final_df.info())


Processing fiat currencies:   0%|          | 0/15 [00:00<?, ?it/s]

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 167733 entries, 0 to 167732
Data columns (total 14 columns):
 #   Column                        Non-Null Count   Dtype  
---  ------                        --------------   -----  
 0   timestamp                     167733 non-null  object 
 1   open                          167733 non-null  float64
 2   high                          167733 non-null  float64
 3   low                           167733 non-null  float64
 4   close                         167733 non-null  float64
 5   volume                        167733 non-null  float64
 6   close_time                    167733 non-null  int64  
 7   quote_asset_volume            167733 non-null  float64
 8   number_of_trades              167733 non-null  int64  
 9   taker_buy_base_asset_volume   167733 non-null  float64
 10  taker_buy_quote_asset_volume  167733 non-null  float64
 11  ignore                        167733 non-null  int64  
 12  fiat_currency                 167733 non-nul

In [14]:
# Check if there are any missing values in the dataset
if final_df.isnull().sum().sum() == 0:
    print("Data check complete: No missing values. All data is clean and ready for analysis.")
else:
    print("Data check complete: There are missing values in the dataset. Further inspection is needed.")
    # Display the columns with missing values and the number of missing values
    missing_data = final_df.isnull().sum()
    print("Columns with missing values:\n", missing_data[missing_data > 0])

# Basic descriptive statistics
final_stats = final_df.describe()
print("Basic statistics generated. Data is ready for further analysis.")
print(final_stats)


Data check complete: No missing values. All data is clean and ready for analysis.
Basic statistics generated. Data is ready for further analysis.
               open          high           low         close        volume  \
count  1.677330e+05  1.677330e+05  1.677330e+05  1.677330e+05  1.677330e+05   
mean   2.746379e+05  2.829375e+05  2.672440e+05  2.754773e+05  2.023497e+10   
std    3.614780e+06  3.729241e+06  3.518946e+06  3.626554e+06  4.182609e+11   
min    6.080000e-06  6.260000e-06  5.050000e-06  6.100000e-06  0.000000e+00   
25%    1.261400e+00  1.300000e+00  1.229000e+00  1.260000e+00  9.023430e+03   
50%    1.395000e+01  1.451000e+01  1.336000e+01  1.393000e+01  1.507700e+05   
75%    9.545000e+01  9.888000e+01  9.152000e+01  9.540000e+01  1.546012e+06   
max    1.063205e+08  1.228866e+08  9.951331e+07  1.068279e+08  3.968651e+13   

         close_time  quote_asset_volume  number_of_trades  \
count  1.677330e+05        1.677330e+05     167733.000000   
mean   1.693020e+12 

# 3. Data Analysis

## 3.1 Overview: Distribution of Cryptocurrency Pairs Across Fiat Currencies


In this section, we examine the relationships between various fiat currencies and leading cryptocurrencies such as BTC and USDT. Our analysis aims to understand the diversity of fiat-crypto pairings across different regions and assess the presence of these pairs over time.

### 3.1.1 Summary Table
We summarize the presence of fiat currencies across different crypto pairs, focusing on the most recent month's data. The table provides insights into which fiat currencies are paired with BTC and USDT, as well as those that do not have such pairs.

In [16]:
import pandas as pd

# Ensure 'timestamp' is in datetime format
final_df['timestamp'] = pd.to_datetime(final_df['timestamp'])

# Filter the data to include only the last month's data
last_month = final_df['timestamp'].max() - pd.DateOffset(months=1)
filtered_df = final_df[final_df['timestamp'] >= last_month]

# Get the list of all fiat currencies in the dataset
all_fiat_currencies = final_df['fiat_currency'].unique()

# Get the list of fiat currencies present in the last month's data
fiat_currencies_last_month = filtered_df['fiat_currency'].unique()

# Identify fiat currencies that have BTC pairs
btc_fiat_currencies = filtered_df[filtered_df['crypto_currency'] == 'BTC']['fiat_currency'].unique()

# Identify fiat currencies that have USDT pairs
usdt_fiat_currencies = filtered_df[filtered_df['crypto_currency'] == 'USDT']['fiat_currency'].unique()

# Identify fiat currencies without BTC pairs
fiat_without_btc = set(fiat_currencies_last_month) - set(btc_fiat_currencies)

# Identify fiat currencies without USDT pairs
fiat_without_usdt = set(fiat_currencies_last_month) - set(usdt_fiat_currencies)

# Identify fiat currencies without either BTC or USDT pairs
fiat_without_btc_or_usdt = fiat_without_btc.union(fiat_without_usdt)

# Counting the number of unique cryptos per fiat currency
crypto_count_per_fiat = final_df.groupby('fiat_currency')['crypto_currency'].nunique()

# Combine all this information into a summary table
summary_table = pd.DataFrame({
    "All Fiat Currencies": [sorted(all_fiat_currencies)],
    "Fiat Currencies in Last Month": [sorted(fiat_currencies_last_month)],
    "Fiat Currencies with BTC Pairs": [sorted(btc_fiat_currencies)],
    "Fiat Currencies with USDT Pairs": [sorted(usdt_fiat_currencies)],
    "Fiat Currencies without BTC Pairs": [sorted(fiat_without_btc)],
    "Fiat Currencies without USDT Pairs": [sorted(fiat_without_usdt)],
    "Fiat Currencies without BTC or USDT Pairs": [sorted(fiat_without_btc_or_usdt)]
})

# Display the summary table as text to make it more readable
for column in summary_table.columns:
    print(f"\n{column} (Total {len(summary_table[column][0])}):")
    print(", ".join(summary_table[column][0]))

# Add a sub-sub-title for the next section
print("\n### Number of Unique Cryptocurrencies per Fiat Currency ###")

# Display the count of unique cryptos per fiat currency in a more readable format
for fiat, count in crypto_count_per_fiat.items():  # Corrected to use items() instead of iteritems()
    print(f"{fiat}: {count} unique cryptocurrencies")



All Fiat Currencies (Total 15):
ARS, AUD, BRL, CZK, EUR, GBP, JPY, MXN, NGN, PLN, RON, RUB, TRY, UAH, ZAR

Fiat Currencies in Last Month (Total 11):
ARS, BRL, CZK, EUR, JPY, MXN, PLN, RON, TRY, UAH, ZAR

Fiat Currencies with BTC Pairs (Total 10):
ARS, BRL, EUR, JPY, MXN, PLN, RON, TRY, UAH, ZAR

Fiat Currencies with USDT Pairs (Total 10):
ARS, BRL, CZK, EUR, MXN, PLN, RON, TRY, UAH, ZAR

Fiat Currencies without BTC Pairs (Total 1):
CZK

Fiat Currencies without USDT Pairs (Total 1):
JPY

Fiat Currencies without BTC or USDT Pairs (Total 2):
CZK, JPY

### Number of Unique Cryptocurrencies per Fiat Currency ###
ARS: 3 unique cryptocurrencies
AUD: 30 unique cryptocurrencies
BRL: 49 unique cryptocurrencies
CZK: 1 unique cryptocurrencies
EUR: 65 unique cryptocurrencies
GBP: 25 unique cryptocurrencies
JPY: 10 unique cryptocurrencies
MXN: 3 unique cryptocurrencies
NGN: 10 unique cryptocurrencies
PLN: 4 unique cryptocurrencies
RON: 4 unique cryptocurrencies
RUB: 25 unique cryptocurrencies
TRY: 

### 3.1.2 Visualization: Fiat Currencies Paired with BTC and USDT


In [17]:
# Diccionario de colores basados en las camisetas de fútbol de cada país (dos colores por país)
country_colors = {
    'USD': ['#B22234', '#3C3B6E'],  # Estados Unidos (rojo y azul)
    'EUR': ['#003399', '#FFD700'],  # Unión Europea (azul y amarillo - colores de la bandera)
    'GBP': ['#FFFFFF', '#CC0000'],  # Reino Unido (blanco y rojo)
    'JPY': ['#BC002D', '#FFFFFF'],  # Japón (rojo y blanco)
    'AUD': ['#FFCC00', '#00843D'],  # Australia (amarillo y verde)
    'CAD': ['#FF0000', '#FFFFFF'],  # Canadá (rojo y blanco)
    'CHF': ['#FF0000', '#FFFFFF'],  # Suiza (rojo y blanco)
    'CNY': ['#FFDE00', '#DE2910'],  # China (amarillo y rojo)
    'INR': ['#FF9933', '#138808'],  # India (naranja y verde)
    'RUB': ['#D52B1E', '#0033A0'],  # Rusia (rojo y azul)
    'BRL': ['#F7E03C', '#00A859'],  # Brasil (amarillo y verde)
    'ARS': ['#74ACDF', '#FFFFFF'],  # Argentina (celeste y blanco)
    'NGN': ['#008751', '#FFFFFF'],  # Nigeria (verde y blanco)
    'TRY': ['#E30A17', '#FFFFFF'],  # Turquía (rojo y blanco)
    'MXN': ['#006847', '#FFFFFF'],  # México (verde y blanco)
    'ZAR': ['#006600', '#FFCC00'],  # Sudáfrica (verde y amarillo)
    'PLN': ['#DC143C', '#FFFFFF'],  # Polonia (rojo y blanco)
    'SEK': ['#FFCD00', '#006AA7'],  # Suecia (amarillo y azul)
    'NOK': ['#BA0C2F', '#00205B'],  # Noruega (rojo y azul)
    'DKK': ['#C60C30', '#FFFFFF'],  # Dinamarca (rojo y blanco)
    'HKD': ['#EE1C25', '#FFFFFF'],  # Hong Kong (rojo y blanco)
    'SGD': ['#E00027', '#FFFFFF'],  # Singapur (rojo y blanco)
    'NZD': ['#000000', '#FFFFFF'],  # Nueva Zelanda (negro y blanco)
    'KRW': ['#C60C30', '#003478'],  # Corea del Sur (rojo y azul)
    'THB': ['#2D2A4A', '#A62712'],  # Tailandia (azul y rojo)
    'MYR': ['#010066', '#FFCC00'],  # Malasia (azul y amarillo)
    'IDR': ['#FF0000', '#FFFFFF'],  # Indonesia (rojo y blanco)
    'PHP': ['#0038A8', '#FFFFFF'],  # Filipinas (azul y blanco)
    'VND': ['#DA251D', '#FFFF00'],  # Vietnam (rojo y amarillo)
    'CZK': ['#DA291C', '#003DA5'],  # República Checa (rojo y azul)
    'HUF': ['#C8102E', '#FFFFFF'],  # Hungría (rojo y blanco)
    'RON': ['#FFD700', '#002D62'],  # Rumanía (amarillo y azul)
    'BGN': ['#00966E', '#FFFFFF'],  # Bulgaria (verde y blanco)
    'HRK': ['#FF0000', '#FFFFFF'],  # Croacia (rojo y blanco)
    'RSD': ['#C6363C', '#FFFFFF'],  # Serbia (rojo y blanco)
    'UAH': ['#FFD700', '#0057B7'],  # Ucrania (amarillo y azul)
    'KZT': ['#00AFCA', '#FFD700'],  # Kazajistán (azul y amarillo)
    'AZN': ['#00B140', '#EF3340'],  # Azerbaiyán (verde y rojo)
    'GEL': ['#DD0034', '#FFFFFF'],  # Georgia (rojo y blanco)
    'BYN': ['#D22630', '#FFFFFF'],  # Bielorrusia (rojo y blanco)
    'EGP': ['#CE1126', '#FFFFFF'],  # Egipto (rojo y blanco)
    'ILS': ['#0038A8', '#FFFFFF'],  # Israel (azul y blanco)
    'SAR': ['#00843D', '#FFFFFF'],  # Arabia Saudita (verde y blanco)
    'AED': ['#000000', '#FFFFFF'],  # Emiratos Árabes Unidos (negro y blanco)
    'QAR': ['#8C1D40', '#FFFFFF'],  # Qatar (granate y blanco)
    'KWD': ['#007A3D', '#FFFFFF'],  # Kuwait (verde y blanco)
    'BHD': ['#8C1D40', '#FFFFFF'],  # Baréin (granate y blanco)
    'OMR': ['#D71920', '#FFFFFF'],  # Omán (rojo y blanco)
    'TND': ['#DA291C', '#FFFFFF'],  # Túnez (rojo y blanco)
    'MAD': ['#C1272D', '#4CBB17'],  # Marruecos (rojo y verde)
    'DZD': ['#007A33', '#FFFFFF'],  # Argelia (verde y blanco)
    'TWD': ['#0033A0', '#FFFFFF'],  # Taiwán (azul y blanco)
    'LKR': ['#FEC334', '#B22222'],  # Sri Lanka (amarillo y rojo)
    'PKR': ['#01411C', '#FFFFFF'],  # Pakistán (verde y blanco)
    'BDT': ['#006A4E', '#FFFFFF'],  # Bangladés (verde y blanco)
    'KES': ['#006600', '#FFFFFF'],  # Kenia (verde y blanco)
    'TZS': ['#008C45', '#FFFFFF'],  # Tanzania (verde y blanco)
    'UGX': ['#FFD100', '#CE1126'],  # Uganda (amarillo y rojo)
    'GHS': ['#006B3F', '#FFCC00'],  # Ghana (verde y amarillo)
    'XAF': ['#FFD700', '#00853F'],  # África Central (amarillo y verde)
    'XOF': ['#FFD700', '#00853F'],  # África Occidental (amarillo y verde)
    'XPF': ['#00467F', '#FFFFFF'],  # Polinesia Francesa (azul y blanco)
    'MUR': ['#EC1C24', '#FFD100'],  # Mauricio (rojo y amarillo)
    'SCR': ['#003DA5', '#FFFFFF'],  # Seychelles (azul y blanco)
    'MGA': ['#E20D18', '#007A33'],  # Madagascar (rojo y verde)
    'ZMW': ['#FF9933', '#008751'],  # Zambia (naranja y verde)
    'MWK': ['#CE1126', '#000000'],  # Malaui (rojo y negro)
    'BWP': ['#00ADEF', '#FFFFFF'],  # Botsuana (azul claro y blanco)
    'NAD': ['#00247D', '#FFD100'],  # Namibia (azul y amarillo)
    'SLL': ['#0072C6', '#FFFFFF'],  # Sierra Leona (azul y blanco)
    'LRD': ['#B22234', '#3C3B6E'],  # Liberia (rojo y azul)
    'LSL': ['#003DA5', '#FFFFFF'],  # Lesoto (azul y blanco)
    'SZL': ['#00247D', '#FFD100'],  # Esuatini (azul y amarillo)
    'MZN': ['#C8102E', '#000000'],  # Mozambique (rojo y negro)
    'BIF': ['#00853F', '#FFFFFF'],  # Burundi (verde y blanco)
    'CDF': ['#007FFF', '#FFD700'],  # Congo (azul y amarillo)
    'DJF': ['#00ADEF', '#FFFFFF'],  # Yibuti (azul claro y blanco)
    'ETB': ['#DA291C', '#007A33'],  # Etiopía (rojo y verde)
    'GNF': ['#FFD100', '#CE1126'],  # Guinea (amarillo y rojo)
    'HTG': ['#00205B', '#CE1126'],  # Haití (azul y rojo)
    'NPR': ['#DC143C', '#003153'],  # Nepal (rojo y azul)
    'PGK': ['#D71920', '#000000'],  # Papúa Nueva Guinea (rojo y negro)
    'SHP': ['#00205B', '#FFFFFF'],  # Santa Helena (azul y blanco)
    'SOM': ['#418FDE', '#FFFFFF'],  # Somalia (azul claro y blanco)
    'SSP': ['#CE1126', '#000000'],  # Sudán del Sur (rojo y negro)
    'SYP': ['#CE1126', '#FFFFFF'],  # Siria (rojo y blanco)
    'TTD': ['#E0001B', '#FFFFFF'],  # Trinidad y Tobago (rojo y blanco)
    'TOP': ['#C8102E', '#FFFFFF'],  # Tonga (rojo y blanco)
    'TWD': ['#0033A0', '#FFFFFF'],  # Taiwán (azul y blanco)
    'VUV': ['#FFD100', '#008751'],  # Vanuatu (amarillo y verde)
    'WST': ['#003DA5', '#FFFFFF'],  # Samoa (azul y blanco)
    'XCD': ['#00205B', '#CE1126'],  # Caribe Oriental (azul y rojo)
    'YER': ['#CE1126', '#FFFFFF'],  # Yemen (rojo y blanco)
}

# Asegúrate de que todos los países presentes en el gráfico tengan colores asignados
for country in fiat_currencies:
    if country not in country_colors:
        country_colors[country] = ['#CCCCCC', '#999999']  # Asignar colores grises por defecto si no está definido


In [18]:
import plotly.graph_objects as go

# Ordenar los datos de mayor a menor
crypto_count_per_fiat_sorted = crypto_count_per_fiat.sort_values(ascending=False)

# Crear un gráfico de barras para mostrar el número de criptomonedas únicas por moneda fiat
fig_crypto_count_per_fiat = go.Figure()

for country in crypto_count_per_fiat_sorted.index:
    # Obtener el color asociado al país (usando el primer color de la lista)
    color = country_colors.get(country, ['#CCCCCC', '#999999'])[0]  # Usar gris si no se encuentra el país
    
    fig_crypto_count_per_fiat.add_trace(go.Bar(
        x=[country],  # Agregar el país como única entrada en el eje X
        y=[crypto_count_per_fiat_sorted[country]],  # Agregar el valor correspondiente
        marker_color=color,  # Asignar el color de la camiseta de fútbol
        name=country
    ))

# Configurar el layout del gráfico
fig_crypto_count_per_fiat.update_layout(
    title='<b>Number of Unique Cryptocurrencies per Fiat Currency<b>',
    title_font_color="#AA322F",  
    xaxis_title='Fiat Currency',
    yaxis_title='Number of Unique Cryptocurrencies',
    xaxis_tickangle=-45,
    showlegend=False  # Ocultar la leyenda si no es necesaria
)

# Mostrar el gráfico
fig_crypto_count_per_fiat.show()


In [19]:
fig_btc_usdt_pairs = go.Figure()

# Agregar las barras para BTC
fig_btc_usdt_pairs.add_trace(go.Bar(
    x=list(fiat_currencies_last_month),
    y=[1 if fiat in btc_fiat_currencies else 0 for fiat in fiat_currencies_last_month],
    name='BTC Pairs',
    marker_color='dodgerblue'
))

# Agregar las barras para USDT
fig_btc_usdt_pairs.add_trace(go.Bar(
    x=list(fiat_currencies_last_month),
    y=[1 if fiat in usdt_fiat_currencies else 0 for fiat in fiat_currencies_last_month],
    name='USDT Pairs',
    marker_color='orange'
))

# Configurar el layout del gráfico
fig_btc_usdt_pairs.update_layout(
    barmode='stack',
    title='<b>Fiat Currencies with BTC and USDT Pairs<b>',
    title_font_color="#AA322F",   
    xaxis_title='Fiat Currency',
    yaxis_title='Presence (1 = Yes, 0 = No)',
    xaxis_tickangle=-45,
)

# Mostrar el gráfico
fig_btc_usdt_pairs.show()

In [22]:
import pandas as pd
import plotly.graph_objects as go

# Asegurarse de que 'timestamp' esté en formato datetime
final_df['timestamp'] = pd.to_datetime(final_df['timestamp'])

# Filtrar los datos para incluir solo los datos del último mes
last_month = final_df['timestamp'].max() - pd.DateOffset(months=1)
filtered_df = final_df[final_df['timestamp'] >= last_month]

# Eliminar duplicados para contar cada par cripto-fiat solo una vez
unique_pairs_df = filtered_df.drop_duplicates(subset=['crypto_currency', 'fiat_currency'])

# Contar la frecuencia de cada criptomoneda en el conjunto de datos filtrados
crypto_frequency = unique_pairs_df['crypto_currency'].value_counts()

# Seleccionar las 15 criptomonedas principales
top_15_cryptos = crypto_frequency.nlargest(15)

# Definir colores para BTC, USDT y Others
crypto_colors = {
    'BTC': '#F7931A',   # Naranja para Bitcoin
    'USDT': '#26A17B',  # Verde para Tether
    'OTHERS': '#B0B0B0'  # Gris para otras criptomonedas
}

# Crear el gráfico de barras de Plotly con un nombre descriptivo
fig_unique_frequency = go.Figure()

for crypto in top_15_cryptos.index:
    color = crypto_colors.get(crypto, crypto_colors['OTHERS'])  # Asignar color de criptomoneda o gris por defecto
    fig_unique_frequency.add_trace(go.Bar(
        x=[crypto],
        y=[top_15_cryptos[crypto]],
        marker_color=color,
        name=crypto
    ))

# Personalizar el diseño del gráfico
fig_unique_frequency.update_layout(
    title="<b>Unique Frequency of Top 15 Cryptocurrencies in the Last Month<b>",
    title_font_color="#AA322F",   
    xaxis_title="Cryptocurrency",
    yaxis_title="Unique Frequency",
    xaxis_tickangle=-45,
    showlegend=False  # Ocultar la leyenda si no es necesaria
)

# Mostrar el gráfico
fig_unique_frequency.show()

# Mensaje de confirmación simple
print("Unique frequency plot of top 15 cryptocurrencies for the last month generated.")


Unique frequency plot of top 15 cryptocurrencies for the last month generated.


In [55]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Ordenar los datos de mayor a menor para el primer gráfico
crypto_count_per_fiat_sorted = crypto_count_per_fiat.sort_values(ascending=False)

# Crear la figura con 1 fila y 2 columnas
fig_comparative_crypto_metrics = make_subplots(rows=1, cols=2, subplot_titles=("Unique Cryptocurrencies per Fiat", 
                                                                              "Frequency of Top 15 Cryptocurrencies"))

# Definir los colores para las criptomonedas, asegurando consistencia con gráficos anteriores
crypto_colors = {
    'BTC': '#F7931A',   # Naranja para Bitcoin
    'USDT': '#26A17B',  # Verde para Tether
    'OTHERS': '#B0B0B0',  # Gris para otras criptomonedas
    # Añadir colores adicionales para otras criptomonedas si es necesario
}

# Gráfico 1: Número de criptomonedas únicas por moneda fiat (ordenado)
for country in crypto_count_per_fiat_sorted.index:
    color = country_colors.get(country, ['#CCCCCC', '#999999'])[0]  # Colores para los países
    fig_comparative_crypto_metrics.add_trace(go.Bar(
        x=[country],  
        y=[crypto_count_per_fiat_sorted[country]],  
        marker_color=color,  
        name=country
    ), row=1, col=1)

# Gráfico 2: Frecuencia única de las 15 principales criptomonedas en el último mes
for crypto in top_15_cryptos.index:
    color = crypto_colors.get(crypto.upper(), 'skyblue')  # Usar los colores definidos para las criptomonedas
    fig_comparative_crypto_metrics.add_trace(go.Bar(
        x=[crypto],
        y=[top_15_cryptos[crypto]],
        marker_color=color,
        name=crypto
    ), row=1, col=2)

# Ajustar el diseño final
fig_comparative_crypto_metrics.update_layout(
    height=600, 
    width=1000, 
    title_text="Comparative Analysis of Cryptoasset Metrics",
    title_font=dict(size=20, color="#AA322F"),
    showlegend=False,
    title_x=0.5  
)

# Mostrar la figura
fig_comparative_crypto_metrics.show()


### 3.1.3 Cross-Sectional Analysis: Unique Cryptocurrency Distribution
Here, we explore the diversity of cryptocurrency pairings across different fiat currencies. We calculate the number of unique cryptocurrencies paired with each fiat currency and present the results with two key visualizations:

Unique Cryptocurrencies per Fiat Currency

This bar chart shows the number of unique cryptocurrencies paired with each fiat currency. The visualization helps highlight which fiat currencies have a wider variety of crypto-asset pairings.

In [23]:
## Heatmap of Top 10 Cryptocurrencies Paired with Fiat Currencies

# This section presents a heatmap that visualizes the presence of trading pairs between the top 10 cryptocurrencies and various fiat currencies. The heatmap offers a clear overview of which fiat currencies are most commonly paired with these leading cryptocurrencies. Additionally, we include a category labeled 'Others' to capture any cryptocurrencies outside the top 10, ensuring a comprehensive view of the dataset.

import pandas as pd
import plotly.graph_objects as go

# Ensure 'timestamp' is in datetime format
final_df['timestamp'] = pd.to_datetime(final_df['timestamp'])

# Count the number of pairs for each cryptocurrency across the entire dataset
crypto_counts = final_df['crypto_currency'].value_counts()

# Identify the top 10 cryptocurrencies based on the entire dataset
top_10_cryptos = crypto_counts.nlargest(10).index.tolist()

# Filter the data to include only the last month's data
last_month = final_df['timestamp'].max() - pd.DateOffset(months=1)
filtered_df = final_df[final_df['timestamp'] >= last_month].copy()  # Use .copy() to avoid the SettingWithCopyWarning

# Group the remaining cryptocurrencies into "Others"
filtered_df.loc[:, 'crypto_category'] = filtered_df['crypto_currency'].apply(
    lambda x: x if x in top_10_cryptos else 'Others'
)

# Create a list of unique categories (top 10 cryptos + 'Others')
categories = top_10_cryptos + ['Others']

# List of all fiat currencies present in the entire dataset
all_fiats = sorted(final_df['fiat_currency'].unique())  # Sort fiat currencies alphabetically

# Initialize an empty matrix with zeros (no pairs) for all fiat currencies
matrix = pd.DataFrame(0, index=categories, columns=all_fiats)

# Fill the matrix with 1 where pairs exist
for _, row in filtered_df.iterrows():
    matrix.loc[row['crypto_category'], row['fiat_currency']] = 1

# Unified color scheme for all cryptos
colorscale = [[0, '#D3D3D3'], [1, '#4682B4']]  # Light gray for no pair, steel blue for all pairs

# Plot using Plotly
fig_heatmap_top10 = go.Figure(data=go.Heatmap(
    z=matrix.values,
    x=matrix.columns,
    y=matrix.index,
    colorscale=colorscale,
    showscale=False,  # Hide color scale bar
))

# Update layout for better readability and custom Y-axis labels
fig_heatmap_top10.update_layout(
    title="<b>Top 10 Crypto-Fiat Pair Presence and 'Others'<b>",
    title_font_color="#AA322F",   
    xaxis_title="Fiat Currency",
    yaxis_title="Cryptocurrency",
    yaxis=dict(
        tickmode='array',
        tickvals=list(range(len(categories))),
        ticktext=[f'<b>{crypto}</b>' if crypto == 'Others' else crypto for crypto in categories],
        tickfont=dict(size=10),
        side='left'
    ),
    xaxis=dict(
        tickmode='array',
        tickvals=list(range(len(all_fiats))),
        ticktext=all_fiats  # Ensure all fiat currencies are shown on the X-axis
    ),
    template="plotly_white"
)

# Show the plot
fig_heatmap_top10.show()


Animated Heatmap of Crypto-Fiat Pairs Over Time

In this section, we extend the heatmap analysis by introducing a time element, creating an animated heatmap that shows the presence of crypto-fiat pairs over a series of months. This visualization helps track changes over time, providing insights into the evolving dynamics of crypto-fiat pairings in the market. The animation allows us to see how the presence of different pairs fluctuates across different time periods, offering a temporal dimension to our analysis.


In [24]:

import pandas as pd
import plotly.graph_objects as go
import warnings
from tqdm.notebook import tqdm  # To show progress bar

# Suppress the SettingWithCopyWarning
warnings.simplefilter(action='ignore', category=pd.errors.SettingWithCopyWarning)

# Ensure 'timestamp' is in datetime format
final_df['timestamp'] = pd.to_datetime(final_df['timestamp'])

# Count the number of pairs for each cryptocurrency across the entire dataset
all_crypto_counts = final_df['crypto_currency'].value_counts()

# Identify the top 10 cryptocurrencies based on the entire dataset
top_10_cryptos = all_crypto_counts.nlargest(10).index.tolist()

# Define categories for Y-axis (top 10 cryptos + 'Others')
categories = top_10_cryptos + ['Others']

# Extract the month from the timestamp
final_df['month'] = final_df['timestamp'].dt.to_period('M')

# Extend the data to include up to 2024-08, even if there are no new data entries
all_months = pd.period_range(final_df['month'].min(), '2024-08', freq='M')

# List of all fiat currencies present in the dataset
all_fiats = sorted(final_df['fiat_currency'].unique())  # Sort fiat currencies alphabetically

# Initialize a list to store all frames
frames = []

# Generate a frame for each month
for month in tqdm(all_months, desc="Generating frames"):
    # Filter the data for the given month
    monthly_data = final_df[final_df['month'] == month].copy()

    # Group the remaining cryptocurrencies into "Others"
    if not monthly_data.empty:
        monthly_data.loc[:, 'crypto_category'] = monthly_data['crypto_currency'].apply(
            lambda x: x if x in top_10_cryptos else 'Others'
        )

    # Initialize an empty matrix with zeros (no pairs)
    matrix = pd.DataFrame(0, index=categories, columns=all_fiats)

    # Fill the matrix with 1 where pairs exist
    if not monthly_data.empty:
        for _, row in monthly_data.iterrows():
            matrix.loc[row['crypto_category'], row['fiat_currency']] = 1

    # Create a frame for this month
    frames.append(go.Frame(
        data=go.Heatmap(
            z=matrix.values,
            x=matrix.columns,
            y=matrix.index,
            colorscale=[[0, '#D3D3D3'], [1, '#4682B4']],  # Light gray for no pair, steel blue for all pairs
            showscale=False
        ),
        name=str(month)
    ))

# Plot using Plotly
fig_heatmap_animated = go.Figure(
    data=frames[0]['data'],  # Use the first month's data as the starting point
    layout=go.Layout(
        title="<b>Top 10 Crypto-Fiat Pair Presence and 'Others' Over Time (All Fiat Currencies)<b>",
        title_font_color="#AA322F",   
        xaxis_title="Fiat Currency",
        yaxis_title="Cryptocurrency",
        yaxis=dict(
            tickmode='array',
            tickvals=list(range(len(categories))),
            ticktext=[f'<b>{crypto}</b>' if crypto == 'Others' else crypto for crypto in categories],
            tickfont=dict(size=10),
            side='left'
        ),
        xaxis=dict(
            tickmode='array',
            tickvals=list(range(len(all_fiats))),
            ticktext=all_fiats  # This is now sorted alphabetically
        ),
        template="plotly_white",
        updatemenus=[dict(type="buttons", showactive=False,
                          buttons=[dict(label="Play",
                                        method="animate",
                                        args=[None, {"frame": {"duration": 500, "redraw": True},
                                                     "fromcurrent": True,
                                                     "transition": {"duration": 300}}]),
                                   dict(label="Pause",
                                        method="animate",
                                        args=[[None], {"frame": {"duration": 0, "redraw": False},
                                                       "mode": "immediate",
                                                       "transition": {"duration": 0}}])])],
        sliders=[{
            'currentvalue': {
                'prefix': 'Month: ',
                'font': {'size': 20}
            },
            'pad': {'b': 10},
            'len': 0.9,
            'x': 0.1,
            'y': 0,
            'steps': [{
                'args': [[str(month)], {
                    'frame': {'duration': 500, 'redraw': True},
                    'mode': 'immediate',
                    'transition': {'duration': 300}
                }],
                'label': str(month),
                'method': 'animate'
            } for month in all_months]
        }]
    ),
    frames=frames  # Add the frames to the figure
)

# Show the plot
fig_heatmap_animated.show()


Generating frames:   0%|          | 0/59 [00:00<?, ?it/s]

## 3.2 USD Volume Analysis
In this section, we download the USD prices of major crypto assets and calculate the transaction volume in USD for crypto-fiat pairs. The following methodology ensures that the data is correctly processed and prepared for volume analysis.

### Block 1: Downloading Prices in USD
First, we use the Coin Metrics API to download historical USD prices for BTC, ETH, and USDT.

In [26]:
pip install coinmetrics-api-client -U

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.7/54.7 kB 2.4 MB/s eta 0:00:00
  Attempting uninstall: typer
    Found existing installation: typer 0.9.0
    Uninstalling typer-0.9.0:
      Successfully uninstalled typer-0.9.0
Note: you may need to restart the kernel to use updated packages.


In [27]:
from coinmetrics.api_client import CoinMetricsClient
import pandas as pd
from tqdm.notebook import tqdm

# Initialize the Coin Metrics client for the Community API
client = CoinMetricsClient()

# Define the assets and metrics
assets = ['btc', 'eth', 'usdt']
metrics = ['PriceUSD']

# Define the start date (January 1, 2019)
start_time = '2019-01-01'

# Prepare the progress bar and download the prices
price_data_frames = []
for asset in tqdm(assets, desc="Downloading prices"):
    # Download the price data for each asset
    price_data = client.get_asset_metrics(assets=[asset], metrics=metrics, frequency='1d', start_time=start_time)
    
    # Convert the data to a Pandas DataFrame and add it to the list
    price_data_frames.append(price_data.to_dataframe())

# Combine all DataFrames into one
price_df = pd.concat(price_data_frames)

# Ensure that the 'PriceUSD' column is numeric
price_df['PriceUSD'] = pd.to_numeric(price_df['PriceUSD'], errors='coerce')


### Block 2: Processing Data and Calculating Volume in USD
Next, we process the data by normalizing time zones, merging the price data with the transaction data, and calculating the volume in USD.

In [28]:
# Normalize time zones
# Convert the time columns to datetime without timezone
filtered_df['timestamp'] = pd.to_datetime(filtered_df['timestamp']).dt.tz_localize(None)
price_df['time'] = pd.to_datetime(price_df['time']).dt.tz_localize(None)

# Filter the DataFrame to include only BTC, ETH, and USDT
filtered_df = final_df[final_df['crypto_currency'].isin(['BTC', 'ETH', 'USDT'])]

# Convert both to lowercase to ensure matching
filtered_df['crypto_currency'] = filtered_df['crypto_currency'].str.lower()
price_df['asset'] = price_df['asset'].str.lower()

# Merge the DataFrames based on 'timestamp', 'crypto_currency', and 'asset'
merged_df = pd.merge(filtered_df, price_df, left_on=['timestamp', 'crypto_currency'], right_on=['time', 'asset'], how='inner')

# Create the 'volumeUSD' column by multiplying volume by the USD price
merged_df['volumeUSD'] = merged_df['volume'] * merged_df['PriceUSD']

# Create a new database with relevant columns
new_base = merged_df[['timestamp', 'crypto_currency', 'volumeUSD', 'fiat_currency']]

# Rename the columns for clarity (optional)
new_base.columns = ['Date', 'Asset', 'VolumeUSD', 'Country']


### 3.2.1 Visualization of the Crypto-Fiat Trading Network

In this section, we will visualize the trading network between cryptocurrencies and fiat currencies. Using network graphs, we will map out the relationships between various assets and countries based on trading volumes. This approach allows us to identify key nodes (either assets or countries) that play a central role in the crypto trading ecosystem.

The graph below illustrates how different cryptocurrencies like BTC, ETH, and USDT interact with fiat currencies across various countries. The size of each node represents its importance within the network, determined by the trading volume. Connections between nodes indicate direct trading pairs, with thicker edges representing higher trading volumes.

This network visualization provides insights into the structure and dynamics of the crypto-fiat trading ecosystem, highlighting the most influential currencies and assets over time.


In [34]:
import igraph as ig
import plotly.graph_objects as go

# Supongamos que 'new_base' ya está cargado en el entorno, aquí replicamos lo necesario para el gráfico

# Extraer los vertices y las aristas a partir de 'new_base'
vertices = set()
edges = []
weights = []

for _, row in new_base.iterrows():
    asset = row['Asset']
    country = row['Country']
    volume = row['VolumeUSD']
    
    vertices.add(asset)
    vertices.add(country)
    edges.append((asset, country))
    weights.append(volume)

# Convertir el conjunto de vertices a una lista
vertices = list(vertices)

# Crear el grafo en igraph
G_ig = ig.Graph()
G_ig.add_vertices(vertices)
G_ig.add_edges(edges)
G_ig.es['weight'] = weights  # Asignar los pesos de las aristas

# Filtrar nodos con grado menor que 3
low_degree_nodes = [v.index for v in G_ig.vs if G_ig.degree(v) < 1]
G_ig.delete_vertices(low_degree_nodes)

# Calcular PageRank para los nodos restantes y aplicar un escalado
pagerank = G_ig.pagerank(weights=G_ig.es['weight'])
max_pagerank = max(pagerank)

# Exagerar las diferencias aplicando una transformación exponencial al PageRank
min_size = 1  # Tamaño mínimo para nodos con solo 3 conexiones
mid_size = 10 # Tamaño para nodos con 4 conexiones
max_size = 40 # Tamaño máximo para nodos con más conexiones y alto PageRank

# Asignar tamaños basados en el número de conexiones y PageRank
vertex_sizes = []
for i in range(len(G_ig.vs)):
    degree = G_ig.degree(i)
    if degree == 3:
        vertex_sizes.append(min_size)
    elif degree == 4:
        vertex_sizes.append(mid_size)
    else:
        vertex_sizes.append(min_size + (pagerank[i] / max_pagerank) ** 0.3 * (max_size - min_size))

# Asignar colores y etiquetas a los nodos
vertex_colors = []
label_colors = []
for i in range(len(G_ig.vs)):
    if G_ig.vs[i]['name'] in new_base['Country'].unique():
        vertex_colors.append('blue')
        label_colors.append('blue')
    else:
        vertex_colors.append('red')
        label_colors.append('red')

# Definir tamaños de las etiquetas basados en PageRank
vertex_labels = [G_ig.vs[i]['name'] for i in range(len(G_ig.vs))]

# Plotear el grafo utilizando Plotly para visualización interactiva
layout = G_ig.layout('fr')  # Usar el layout Fruchterman-Reingold
Xn = [layout[k][0] for k in range(len(layout))]
Yn = [layout[k][1] for k in range(len(layout))]
Xe = []
Ye = []
for e in G_ig.es:
    Xe.extend([layout[e.source][0], layout[e.target][0], None])
    Ye.extend([layout[e.source][1], layout[e.target][1], None])

fig = go.Figure()

# Agregar aristas
fig.add_trace(go.Scatter(x=Xe, y=Ye,
                         mode='lines',
                         line=dict(width=1, color='grey'),
                         hoverinfo='none'
                         ))

# Agregar nodos
fig.add_trace(go.Scatter(x=Xn, y=Yn,
                         mode='markers+text',
                         marker=dict(symbol='circle-dot',
                                     size=vertex_sizes,
                                     color=vertex_colors,
                                     line=dict(color='black', width=0.5)),
                         text=vertex_labels,
                         textposition='top center',
                         textfont=dict(size=10),
                         hoverinfo='text'
                         ))

fig.update_layout(showlegend=False)

In [30]:
new_base['Year'] = pd.to_datetime(new_base['Date']).dt.year

In [31]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import igraph as ig

# Definir el diccionario para acumular volúmenes
total_volume_dict = {}

# Calcular los volúmenes totales por nodo
for _, row in new_base.iterrows():
    asset = row['Asset']
    country = row['Country']
    volume = row['VolumeUSD']
    
    # Acumular volúmenes
    total_volume_dict[asset] = total_volume_dict.get(asset, 0) + volume
    total_volume_dict[country] = total_volume_dict.get(country, 0) + volume

# Determinar el volumen máximo
max_volume = max(total_volume_dict.values())

# Clasificación de monedas fiat en AEs y EMDEs
aes_currencies = ['USD', 'EUR', 'GBP', 'JPY', 'AUD', 'CZK']  # Economías Avanzadas
emdes_currencies = ['NGN', 'RUB', 'TRY', 'ZAR', 'UAH', 'BRL', 'ERN', 'PLN', 'RON', 'ARS', 'MXN']  # Mercados Emergentes

aes_color = '#AA322F'  # Rojo oscuro para AEs
emdes_color = '#6FA5E2'  # Azul pastel más oscuro para EMDEs
crypto_color = '#D3D3D3'  # Gris claro para criptomonedas

# Crear una figura con 4 subplots (2x2)
fig_network_evolution = make_subplots(rows=2, cols=2, subplot_titles=("2021", "2022", "2023", "2024"),
                                      vertical_spacing=0.1)

# Definir los años para cada subplot
years = [2021, 2022, 2023, 2024]
positions = [(1, 1), (1, 2), (2, 1), (2, 2)]

for year, pos in zip(years, positions):
    yearly_data = new_base[new_base['Year'] == year]
    vertices = set()
    edges = []
    weights = []
    
    for _, row in yearly_data.iterrows():
        asset = row['Asset']
        country = row['Country']
        volume = row['VolumeUSD']
        
        vertices.add(asset)
        vertices.add(country)
        edges.append((asset, country))
        weights.append(volume)
    
    vertices = list(vertices)
    G_ig = ig.Graph()
    G_ig.add_vertices(vertices)
    G_ig.add_edges(edges)
    G_ig.es['weight'] = weights
    
    layout = G_ig.layout('circle')
    Xn = [layout[k][0] for k in range(len(layout))]
    Yn = [layout[k][1] for k in range(len(layout))]
    Xe = []
    Ye = []
    for e in G_ig.es:
        Xe.extend([layout[e.source][0], layout[e.target][0], None])
        Ye.extend([layout[e.source][1], layout[e.target][1], None])
    
    vertex_sizes = [(total_volume_dict.get(v, 0) / max_volume) * 40 + 10 for v in G_ig.vs['name']]
    vertex_colors = [aes_color if v in aes_currencies else emdes_color if v in emdes_currencies else '#D3D3D3' for v in G_ig.vs['name']]  # Criptomonedas en gris
    
    # Agregar nodos al subplot correspondiente
    fig_network_evolution.add_trace(go.Scatter(x=Xn, y=Yn,
                                               mode='markers+text',
                                               marker=dict(symbol='circle',
                                                           size=vertex_sizes,
                                                           color=vertex_colors,
                                                           line=dict(color='black', width=0.5)),
                                               text=G_ig.vs['name'],
                                               textposition='top center',
                                               textfont=dict(size=10),
                                               hoverinfo='text'),
                                    row=pos[0], col=pos[1])
    
    # Agregar aristas con grosor específico para cada traza
    for i, e in enumerate(G_ig.es):
        fig_network_evolution.add_trace(go.Scatter(x=[layout[e.source][0], layout[e.target][0], None],
                                                   y=[layout[e.source][1], layout[e.target][1], None],
                                                   mode='lines',
                                                   line=dict(width=(weights[i] / max(weights)) * 5, color='grey'),
                                                   hoverinfo='none'),
                                        row=pos[0], col=pos[1])

# Ajustar el diseño de la figura
fig_network_evolution.update_layout(height=800, width=800, showlegend=False,
                                    title_text="<b>Annual Evolution of the Crypto and Fiat Network<b>",
                                    title_font=dict(size=20, color="#AA322F"),
                                    xaxis=dict(showticklabels=False, zeroline=False),
                                    yaxis=dict(showticklabels=False, zeroline=False))

# Aplicar eliminación de escalas a todos los subplots
for i in range(1, 5):
    fig_network_evolution.update_xaxes(showticklabels=False, row=(i+1)//2, col=(i-1)%2 + 1)
    fig_network_evolution.update_yaxes(showticklabels=False, row=(i+1)//2, col=(i-1)%2 + 1)

# Mostrar la figura
fig_network_evolution.show()

In [32]:
import igraph as ig
import plotly.graph_objects as go
import pandas as pd

# Asegúrate de que la columna de meses exista
if 'Date' in new_base.columns:
    new_base['Month'] = pd.to_datetime(new_base['Date']).dt.to_period('M')

# Definir los colores
aes_color = '#AA322F'  # Rojo oscuro para AEs
emdes_color = '#6FA5E2'  # Azul pastel para EMDEs
crypto_color = '#D3D3D3'  # Gris claro para criptomonedas
inactive_color = '#D3D3D3'  # Gris claro tenue para nodos inactivos

x_range = [-1.5, 1.5]
y_range = [-1.5, 1.5]

# Listas de nodos para AEs y EMDEs
aes_nodes = sorted(set(new_base[new_base['Country'].isin(aes_fiat_currencies)]['Country'].unique()))
emdes_nodes = sorted(set(new_base[new_base['Country'].isin(emdes_fiat_currencies)]['Country'].unique()))
crypto_nodes = sorted(set(new_base['Asset'].unique()))

# Definir la lista de meses que quieres analizar
months = sorted(new_base['Month'].unique())

# Estados iniciales de los nodos (todos apagados)
node_states = {node: inactive_color for node in aes_nodes + emdes_nodes + crypto_nodes}

frames = []
previous_nodes = set()

for month in months:
    monthly_data = new_base[new_base['Month'] == month]
    vertices = set()
    edges = []
    weights = []
    
    for _, row in monthly_data.iterrows():
        asset = row['Asset']
        country = row['Country']
        volume = row['VolumeUSD']
        
        vertices.add(asset)
        vertices.add(country)
        edges.append((asset, country))
        weights.append(volume)
    
    current_nodes = vertices
    added_nodes = current_nodes - previous_nodes
    removed_nodes = previous_nodes - current_nodes
    
    # Actualizar el estado de los nodos
    for node in added_nodes:
        if node in aes_nodes:
            node_states[node] = aes_color  # Encender en color rojo oscuro
        elif node in emdes_nodes:
            node_states[node] = emdes_color  # Encender en color azul pastel
        else:
            node_states[node] = inactive_color  # Encender en gris claro
    
    for node in removed_nodes:
        node_states[node] = inactive_color  # Volver al gris claro tenue si desaparece
    
    vertices = list(vertices)
    G_ig = ig.Graph()
    G_ig.add_vertices(vertices)
    G_ig.add_edges(edges)
    G_ig.es['weight'] = weights
    
    layout = G_ig.layout('circle')
    Xn = [layout[k][0] for k in range(len(layout))]
    Yn = [layout[k][1] for k in range(len(layout))]
    Xe = []
    Ye = []
    for e in G_ig.es:
        Xe.extend([layout[e.source][0], layout[e.target][0], None])
        Ye.extend([layout[e.source][1], layout[e.target][1], None])
    
    vertex_sizes = [(total_volume_dict.get(v, 0) / max_volume) * 40 + 10 for v in G_ig.vs['name']]
    
    vertex_colors = []
    vertex_shapes = []
    for v in G_ig.vs['name']:
        if v in aes_nodes:
            vertex_colors.append(aes_color)
            vertex_shapes.append('triangle-up')
        elif v in emdes_nodes:
            vertex_colors.append(emdes_color)
            vertex_shapes.append('triangle-up')
        else:
            vertex_colors.append(crypto_color)
            vertex_shapes.append('circle')
    
    fig_network_evolution = go.Scatter(x=Xn, y=Yn,
                                       mode='markers+text',
                                       marker=dict(symbol=vertex_shapes,
                                                   size=vertex_sizes,
                                                   color=vertex_colors,
                                                   line=dict(color='black', width=0.5)),
                                       text=G_ig.vs['name'],
                                       textposition='top center',
                                       textfont=dict(size=10),
                                       hoverinfo='text'
                                       )

    edge_trace = go.Scatter(x=Xe, y=Ye,
                            mode='lines',
                            line=dict(width=1, color='grey'),
                            hoverinfo='none')

    aes_annotations = [
        dict(
            xref='paper', yref='paper', x=-0.3, y=1.03 - i * 0.045, showarrow=False,
            text=node,
            font=dict(size=11, color=node_states[node]),
            align="left"
        ) for i, node in enumerate(aes_nodes)
    ]

    emdes_annotations = [
        dict(
            xref='paper', yref='paper', x=-0.15, y=1.03 - i * 0.045, showarrow=False,
            text=node,
            font=dict(size=11, color=node_states[node]),
            align="left"
        ) for i, node in enumerate(emdes_nodes)
    ]

    frame_annotations = aes_annotations + emdes_annotations

    frames.append(go.Frame(data=[fig_network_evolution, edge_trace], name=str(month), layout=go.Layout(annotations=frame_annotations)))

    previous_nodes = current_nodes

layout = go.Layout(
    title="Crypto Trading Network Over Time",
    showlegend=False,
    xaxis=dict(range=x_range, autorange=False),
    yaxis=dict(range=y_range, autorange=False),
    updatemenus=[{
        "buttons": [
            {
                "args": [None, {"frame": {"duration": 1000, "redraw": True},
                            "fromcurrent": True, "transition": {"duration": 300}}],
                "label": "Play",
                "method": "animate"
            },
            {
                "args": [[None], {"frame": {"duration": 0, "redraw": True},
                                "mode": "immediate", "transition": {"duration": 0}}],
                "label": "Pause",
                "method": "animate"
            }
        ],
        "direction": "left",
        "pad": {"r": 10, "t": 87},
        "showactive": False,
        "type": "buttons",
        "x": 0.1,
        "xanchor": "right",
        "y": 0,
        "yanchor": "top"
    }],
    sliders=[{
        "steps": [
            {
                "args": [[str(month)], {"frame": {"duration": 300, "redraw": True},
                                        "mode": "immediate", "transition": {"duration": 300}}],
                "label": str(month),
                "method": "animate"
            } for month in months
        ],
        "currentvalue": {"prefix": "Month: ", "visible": True, "xanchor": "center"},
        "transition": {"duration": 300},
        "x": 0.1,
        "xanchor": "center",
        "y": -0.1,
        "yanchor": "top"
    }]
)

fig_crypto_trading_network = go.Figure(
    data=[frames[0].data[0], frames[0].data[1]],
    layout=layout,
    frames=frames
)

fig_crypto_trading_network.show()

### Comparative Analysis of Cryptoasset Exchange Volumes by Cryptocurrency and Country

In this section, we present a comprehensive analysis of cryptoasset exchange volumes, segmented by both individual cryptocurrencies and by the countries where these exchanges occur. This dual approach allows us to gain insights into the following aspects:

1. **Volume Distribution by Cryptocurrency**: Understanding which cryptocurrencies (e.g., Bitcoin, Ethereum, Tether) dominate the trading volumes over time. This perspective highlights the market's preference and the overall activity of different digital assets.

2. **Volume Distribution by Country**: Analyzing the exchange volumes in different countries, which reveals how local markets engage with cryptoassets. This view helps identify key markets and the geographical spread of cryptocurrency adoption.

The analysis is visualized through a stacked bar chart with two subplots:
- The first subplot shows the exchange volumes categorized by cryptocurrency.
- The second subplot displays the exchange volumes segmented by country.

This combined visualization provides a holistic view of the cryptoasset landscape, allowing for a deeper understanding of the interplay between different cryptocurrencies and the countries where they are most actively traded.


In [45]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import pandas as pd

# Ensure 'Date' is in datetime format and create a 'Month' column
new_base['Month'] = pd.to_datetime(new_base['Date']).dt.to_period('M')

# Group the data by month and country, summing up the volumes in USD
grouped_data_countries = new_base.groupby(['Month', 'Country'])['VolumeUSD'].sum().unstack().fillna(0)

# Group the data by month and cryptocurrency, summing up the volumes in USD
grouped_data_crypto = new_base.groupby(['Month', 'Asset'])['VolumeUSD'].sum().unstack().fillna(0)

# Define colors for each cryptocurrency
crypto_colors = {
    'btc': '#F7931A',   # Orange for Bitcoin
    'eth': '#627EEA',   # Blue for Ethereum
    'usdt': '#26A17B',  # Green for Tether
}

# Create the figure with 1 row and 2 columns
fig_comparative_crypto_volumes = make_subplots(rows=1, cols=2, subplot_titles=("by Cryptocurrency", "by Country"))

# Add traces for cryptocurrency volumes
for crypto in grouped_data_crypto.columns:
    fig_comparative_crypto_volumes.add_trace(go.Bar(
        x=grouped_data_crypto.index.astype(str),  # Convert the index (months) to string for proper display
        y=grouped_data_crypto[crypto],
        name=crypto,
        marker_color=crypto_colors.get(crypto, '#B0B0B0')  # Assign color or default to grey if not found
    ), row=1, col=1)

# Add traces for country volumes
for idx, country in enumerate(grouped_data_countries.columns):
    color = country_colors[country][idx % 2]
    fig_comparative_crypto_volumes.add_trace(go.Bar(
        x=grouped_data_countries.index.astype(str),  # Convert the index (months) to string for proper display
        y=grouped_data_countries[country],
        name=country,
        marker_color=color  # Assign the color based on the country's color scheme
    ), row=1, col=2)

# Configure the layout for the combined figure
fig_comparative_crypto_volumes.update_layout(
    barmode='stack',  # Ensure the bars are stacked
    height=600, 
    width=1000, 
    title_text="Comparative Analysis of Cryptoasset Exchange Volumes by Cryptocurrency and Country",
    title_font=dict(size=20, color="#AA322F"),
    showlegend=True,
    title_x=0.5,  # Center the title
    legend_tracegroupgap=180,  # Visually separate the legends of the subplots
    xaxis_tickangle=-45  # Rotate the x-axis labels for better readability
)

# Show the combined figure
fig_comparative_crypto_volumes.show()

### Analysis of Cryptoasset Exchange Volumes by Type of Economy

In this section, we explore how the exchange volumes of cryptoassets differ across two major types of economies: Advanced Economies (AEs) and Emerging Market and Developing Economies (EMDEs). This analysis is crucial for understanding the dynamics and adoption patterns of cryptocurrencies in different economic contexts.

#### Classification of Economies:
- **Advanced Economies (AEs):** These include countries with well-developed financial markets, high levels of income, and significant global economic influence. Examples include the United States (USD), the Eurozone (EUR), and Japan (JPY).
- **Emerging Market and Developing Economies (EMDEs):** These economies are characterized by rapid growth and industrialization, but often have less mature financial systems compared to AEs. Examples include Brazil (BRL), South Africa (ZAR), and Argentina (ARS).

#### Key Aspects of the Analysis:
- **Volume Segmentation by Economy Type:** The analysis segregates the exchange volumes into those conducted in AEs and those in EMDEs. This helps us observe how economic conditions influence the trading activity of cryptoassets.
- **Focus on Major Cryptocurrencies:** The study focuses primarily on Bitcoin (BTC) and Tether (USDT), which are two of the most traded cryptoassets globally. Other cryptocurrencies are grouped under the "Others" category for simplification.
- **Time Frame:** The analysis covers data starting from January 2022, which allows us to capture recent trends and market behaviors in the evolving landscape of digital assets.

By examining these factors, we can derive insights into the differing roles that cryptoassets play in advanced versus emerging economies, and how these markets might evolve in the future.


In [48]:
import pandas as pd

# Assuming the combined DataFrame `merged_df` is already loaded
# Convert the dates to datetime format if not already done
merged_df['timestamp'] = pd.to_datetime(merged_df['timestamp'])

# Classification of fiat currencies into AEs and EMDEs
aes_currencies = ['USD', 'EUR', 'GBP', 'JPY', 'AUD', 'CZK']  # Advanced Economies
emdes_currencies = ['NGN', 'RUB', 'TRY', 'ZAR', 'UAH', 'BRL', 'ERN', 'PLN', 'RON', 'ARS', 'MXN']  # Emerging Markets

# Calculate the volume in USD (this should already be done in `merged_df`)
merged_df['volumeUSD'] = merged_df['volume'] * merged_df['PriceUSD']

# Select only the necessary columns
filtered_df = merged_df[['timestamp', 'fiat_currency', 'crypto_currency', 'volumeUSD']]

# Apply a date filter to include only data from 2022 onwards
filtered_df = filtered_df[filtered_df['timestamp'] >= '2022-01-01']

# Ensure all cryptocurrency codes are in uppercase
filtered_df['crypto_currency'] = filtered_df['crypto_currency'].str.upper()

# Group all cryptocurrencies that are not BTC or USDT into "Others"
filtered_df['crypto_currency'] = filtered_df['crypto_currency'].apply(lambda x: x if x in ['BTC', 'USDT'] else 'OTHERS')

# Split the DataFrame into AEs and EMDEs
aes_df = filtered_df[filtered_df['fiat_currency'].isin(aes_currencies)]
emdes_df = filtered_df[filtered_df['fiat_currency'].isin(emdes_currencies)]

# Group by month and 'crypto_currency', and sum 'volumeUSD' for AEs and EMDEs
aes_grouped = aes_df.groupby([pd.Grouper(key='timestamp', freq='ME'), 'crypto_currency']).sum().reset_index()
emdes_grouped = emdes_df.groupby([pd.Grouper(key='timestamp', freq='ME'), 'crypto_currency']).sum().reset_index()

import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Create the subplots side by side with a suitable size
fig_vol_type_econ = make_subplots(rows=1, cols=2, shared_yaxes=True, subplot_titles=("AEs", "EMDEs"))

# Define colors for BTC, USDT, and Others
colors = {
    'BTC': '#F7931A',   # Orange for Bitcoin
    'USDT': '#26A17B',  # Green for Tether
    'OTHERS': '#B0B0B0'  # Grey for other cryptocurrencies
}

# Ensure the order of the bars: BTC (first), USDT (second), Others (third)
order = ['BTC', 'USDT', 'OTHERS']

# Add traces for AEs
for crypto in order:
    if crypto in aes_grouped['crypto_currency'].unique():
        df_crypto = aes_grouped[aes_grouped['crypto_currency'] == crypto]
        fig_vol_type_econ.add_trace(go.Bar(
            x=df_crypto['timestamp'],
            y=df_crypto['volumeUSD'],
            name=crypto.upper(),
            marker_color=colors.get(crypto.upper(), '#000000'),
            showlegend=True
        ), row=1, col=1)

# Add traces for EMDEs
for crypto in order:
    if crypto in emdes_grouped['crypto_currency'].unique():
        df_crypto = emdes_grouped[emdes_grouped['crypto_currency'] == crypto]
        fig_vol_type_econ.add_trace(go.Bar(
            x=df_crypto['timestamp'],
            y=df_crypto['volumeUSD'],
            name=crypto.upper(),
            marker_color=colors.get(crypto.upper(), '#000000'),
            showlegend=False  # Do not show the legend twice
        ), row=1, col=2)

# Customize the chart layout to fit the page width
fig_vol_type_econ.update_layout(
    title='<b>Cryptoasset Exchange Volumes by Cryptocurrency for AEs and EMDEs<b>',
    title_font_color="#AA322F",
    xaxis_title='Date',
    yaxis_title='Volume (USD)',
    barmode='stack',
    height=500,  # Adjust the height of the chart to make it more compact
    width=800,  # Adjust the width of the chart to fit the Kaggle page
    margin=dict(l=20, r=20, t=50, b=20),  # Adjust margins to maximize available space
    title_font=dict(size=14),  # Reduce title font size to save space
    font=dict(size=10)  # Reduce the general font size to fit better on the page
)

# Display the chart
fig_vol_type_econ.show()


### 2024 Cryptoasset Exchange Volumes: AEs vs. EMDEs
This section focuses on the distribution of cryptoasset exchange volumes in 2024 across Advanced Economies (AEs) and Emerging Market and Developing Economies (EMDEs). The stacked bar chart highlights the percentage share of Bitcoin (BTC), Tether (USDT), and other cryptocurrencies in the total trading volume for each economic category.

In [49]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Filtrar los datos para incluir solo los registros de 2024
aes_grouped_2024 = aes_grouped[aes_grouped['timestamp'].dt.year == 2024]
emdes_grouped_2024 = emdes_grouped[emdes_grouped['timestamp'].dt.year == 2024]

# Sumarizar los volúmenes a nivel anual por criptomoneda
aes_annual = aes_grouped_2024.groupby('crypto_currency')['volumeUSD'].sum().reset_index()
emdes_annual = emdes_grouped_2024.groupby('crypto_currency')['volumeUSD'].sum().reset_index()

# Calcular el volumen total anual para cada tipo de economía
aes_total_annual = aes_annual['volumeUSD'].sum()
emdes_total_annual = emdes_annual['volumeUSD'].sum()

# Calcular los porcentajes de cada criptomoneda en el total anual
aes_annual['percentage'] = aes_annual['volumeUSD'] / aes_total_annual * 100
emdes_annual['percentage'] = emdes_annual['volumeUSD'] / emdes_total_annual * 100

# Crear los subplots uno al lado del otro con un tamaño más adecuado
fig_stacked_bar_crypto_volumes_2024 = make_subplots(rows=1, cols=2, shared_yaxes=True, subplot_titles=("AEs", "EMDEs"))

# Definir colores para BTC, USDT y Others
colores = {
    'BTC': '#F7931A',   # Naranja para Bitcoin
    'USDT': '#26A17B',  # Verde para Tether
    'OTHERS': '#B0B0B0'  # Gris para otras criptomonedas
}

# Asegurar el orden de las barras: BTC (primero), USDT (segundo), Others (tercero)
order = ['BTC', 'USDT', 'OTHERS']

# Agregar trazas para AEs
for crypto in order:
    if crypto in aes_annual['crypto_currency'].unique():
        df_crypto = aes_annual[aes_annual['crypto_currency'] == crypto]
        fig_stacked_bar_crypto_volumes_2024.add_trace(go.Bar(
            x=['AEs'],
            y=df_crypto['percentage'],
            name=crypto.upper(),
            marker_color=colores.get(crypto.upper(), '#000000'),
            showlegend=True
        ), row=1, col=1)

# Agregar trazas para EMDEs
for crypto in order:
    if crypto in emdes_annual['crypto_currency'].unique():
        df_crypto = emdes_annual[emdes_annual['crypto_currency'] == crypto]
        fig_stacked_bar_crypto_volumes_2024.add_trace(go.Bar(
            x=['EMDEs'],
            y=df_crypto['percentage'],
            name=crypto.upper(),
            marker_color=colores.get(crypto.upper(), '#000000'),
            showlegend=False  # No mostrar leyenda dos veces
        ), row=1, col=2)

# Personalizar el diseño del gráfico para ajustarlo al ancho de la página
fig_stacked_bar_crypto_volumes_2024.update_layout(
    title='<b>Stacked Bar Chart: Cryptoasset Exchange Volumes by Cryptocurrency for AEs and EMDEs (2024 Annual)<b>',
    title_font_color="#AA322F",    
    yaxis_title='Percentage of Total Annual Volume',
    barmode='stack',
    height=500,  # Ajustar la altura del gráfico para que sea más compacto
    width=800,  # Ajustar el ancho del gráfico para que quepa en la página de Kaggle
    margin=dict(l=20, r=20, t=50, b=20),  # Ajustar los márgenes para maximizar el espacio disponible
    title_font=dict(size=14),  # Reducir el tamaño de la fuente del título para ahorrar espacio
    font=dict(size=10),  # Reducir el tamaño general de la fuente para encajar mejor en la página
    annotations=[
        go.layout.Annotation(
            text="Note: Stacked Bar Chart, Data from 2024 Only",
            x=0.5,
            y=-0.15,
            showarrow=False,
            xref="paper",
            yref="paper",
            font=dict(size=10, color="grey"),
            align="center"
        )
    ]
)

# Mostrar el gráfico
fig_stacked_bar_crypto_volumes_2024.show()

## Appendix: Automating Graph Exports

This appendix covers the automation of exporting graphs to different platforms. It includes two main subsections: one for publishing graphs on GitHub and another (to be added) for exporting to Plotly Studio Chart.

### Subsection 1: Publishing Graphs on Plotty

In [51]:
!pip install chart-studio --quiet

In [52]:
from kaggle_secrets import UserSecretsClient
user_secrets = UserSecretsClient()
secret_key = user_secrets.get_secret("CHARTSTUDIO_BCRA_API_KEY")

import chart_studio.plotly as py
import chart_studio.tools as tls

# Configurar las credenciales de Plotly
tls.set_credentials_file(username='crypto-financial-stability-monitor', api_key=secret_key)

In [56]:
# Figure 2
py.plot(fig_comparative_crypto_metrics, filename='comparative-crypto-metrics', auto_open=False)

'https://plotly.com/~crypto-financial-stability-monitor/4160/'

In [57]:
#Figure 3
py.plot(fig_heatmap_animated, filename='animated-heatmap-crypto-fiat-over-time', auto_open=False)

'https://plotly.com/~crypto-financial-stability-monitor/4043/'

In [58]:
# Figure 5
py.plot(fig_comparative_crypto_volumes, filename='comparative-crypto-volumes-by-crypto-and-country', auto_open=False)

'https://plotly.com/~crypto-financial-stability-monitor/4169/'

In [59]:
#Figure 6
py.plot(fig_vol_type_econ, filename='crypto-volumes-by-economy-type', auto_open=False)

'https://plotly.com/~crypto-financial-stability-monitor/4049/'

In [60]:
#Figure 7
py.plot(fig_stacked_bar_crypto_volumes_2024, filename='stacked-bar-crypto-volumes-2024', auto_open=False)

'https://plotly.com/~crypto-financial-stability-monitor/4172/'

### Subsection 2: Publishing Graphs on GitHub

This subsection outlines the steps to automate the export of your Plotly graphs to HTML files and publish them to a GitHub repository.

#### Steps:

1. **Export Graphs to HTML**: Save the generated graphs as HTML files.
2. **GitHub Setup**: Configure GitHub credentials and clone the repository.
3. **Move Files to Repository**: Copy the HTML files to the cloned repository.
4. **Commit and Push**: Commit and push the files to GitHub.


In [ ]:
import os
import git
from kaggle_secrets import UserSecretsClient

# Retrieve GitHub token securely from Kaggle secrets
user_secrets = UserSecretsClient()
GITHUB_TOKEN = user_secrets.get_secret("GITHUB_TOKEN")

# Set up the repository URL using the secured token
REPO_URL = "https://{}@github.com/emigiupponi/CryptoFiatVisualizer.git".format(GITHUB_TOKEN)

# Clone the repository if not already done
if not os.path.exists('repo'):
    repo = git.Repo.clone_from(REPO_URL, 'repo')

repo = git.Repo('repo')

# Exportar los gráficos a HTML con tamaño ajustado
fig_network_evolution.update_layout(width=300, height=200)
fig_vol_type_econ.update_layout(width=300, height=200)
fig_heatmap_animated.update_layout(width=300, height=200)
fig_comparative_crypto_metrics.update_layout(width=300, height=200)
fig_comparative_crypto_volumes.update_layout(width=300, height=200)
fig_stacked_bar_crypto_volumes_2024.update_layout(width=300, height=200)

fig_network_evolution.write_html("fig_network_evolution.html", include_plotlyjs='cdn', full_html=False, config={'responsive': True})
fig_vol_type_econ.write_html("fig_vol_type_econ.html", include_plotlyjs='cdn', full_html=False, config={'responsive': True})
fig_heatmap_animated.write_html("fig_heatmap_animated.html", include_plotlyjs='cdn', full_html=False, config={'responsive': True})
fig_comparative_crypto_metrics.write_html("fig_comparative_crypto_metrics.html", include_plotlyjs='cdn', full_html=False, config={'responsive': True})
fig_comparative_crypto_volumes.write_html("fig_comparative_crypto_volumes.html", include_plotlyjs='cdn', full_html=False, config={'responsive': True})
fig_stacked_bar_crypto_volumes_2024.write_html("fig_stacked_bar_crypto_volumes_2024.html", include_plotlyjs='cdn', full_html=False, config={'responsive': True})

# Move HTML files to the repo
os.system('cp *.html repo/')

# Commit and push to GitHub
repo.index.add([
    'fig_network_evolution.html',
    'fig_vol_type_econ.html',
    'fig_heatmap_animated.html',
    'fig_comparative_crypto_metrics.html',
    'fig_comparative_crypto_volumes.html',
    'fig_stacked_bar_crypto_volumes_2024.html'
])

repo.index.commit("Add resized crypto fiat visualizations")
repo.remote(name='origin').push()


New format for GitHub page

In [61]:
import igraph as ig
import plotly.graph_objects as go

# Suponiendo que 'info_pares' contiene el diccionario con la información de los pares de divisas
info_pares = obtener_info_pares_binance()

# Listas de monedas fiat para AEs y EMDEs
aes_fiat_currencies = ['USD', 'EUR', 'GBP', 'JPY', 'AUD', 'CAD', 'CHF', 'CZK']
emdes_fiat_currencies = [
    'BRL', 'ARS', 'NGN', 'TRY', 'MXN', 'ZAR', 'PLN', 'RUB', 'RON', 'UAH'
]

# Colores
aes_color = '#AA322F'  # Rojo oscuro para AEs
emdes_color = '#6FA5E2'  # Azul pastel más oscuro para EMDEs
crypto_color = '#D3D3D3'  # Gris claro para criptomonedas
crypto_label_color = '#A9A9A9'  # Gris un poco más oscuro para etiquetas de criptomonedas

# Extraer los vertices y las aristas a partir de 'info_pares'
vertices = set()
edges = []

for symbol, details in info_pares.items():
    base_currency = details['base_currency']
    quote_currency = details['quote_currency']
    vertices.add(base_currency)
    vertices.add(quote_currency)
    edges.append((base_currency, quote_currency))

# Convertir el conjunto de vertices a una lista
vertices = list(vertices)

# Crear el grafo en igraph
G_ig = ig.Graph()
G_ig.add_vertices(vertices)
G_ig.add_edges(edges)

# Filtrar nodos con grado menor que 3
low_degree_nodes = [v.index for v in G_ig.vs if G_ig.degree(v) < 3]
G_ig.delete_vertices(low_degree_nodes)

# Recalcular el PageRank después de eliminar los nodos de bajo grado
pagerank = G_ig.pagerank()
max_pagerank = max(pagerank)

# Exagerar las diferencias aplicando una transformación exponencial al PageRank
min_size = 1  # Tamaño mínimo para nodos con solo 3 conexiones
mid_size = 10 # Tamaño para nodos con 4 conexiones
max_size = 40 # Tamaño máximo para nodos con más conexiones y alto PageRank

# Asignar tamaños basados en el número de conexiones y PageRank
vertex_sizes = []
for i in range(len(G_ig.vs)):
    degree = G_ig.degree(i)
    if degree == 3:
        vertex_sizes.append(min_size)
    elif degree == 4:
        vertex_sizes.append(mid_size)
    else:
        vertex_sizes.append(min_size + (pagerank[i] / max_pagerank) ** 0.3 * (max_size - min_size))

# Encontrar las criptomonedas con los 5 mayores valores de PageRank
top_5_cryptos = sorted(range(len(pagerank)), key=lambda i: pagerank[i], reverse=True)[:5]

# Asignar colores a los nodos y etiquetas: AEs, EMDEs y criptomonedas
vertex_colors = []
label_colors = []
for i in range(len(G_ig.vs)):
    if G_ig.vs[i]['name'] in aes_fiat_currencies:
        vertex_colors.append(aes_color)
        label_colors.append(aes_color)
    elif G_ig.vs[i]['name'] in emdes_fiat_currencies:
        vertex_colors.append(emdes_color)
        label_colors.append(emdes_color)
    else:
        vertex_colors.append(crypto_color)
        label_colors.append(crypto_label_color)

# Asignar forma a los nodos
vertex_shapes = [
    'triangle-up' if G_ig.vs[i]['name'] in aes_fiat_currencies or G_ig.vs[i]['name'] in emdes_fiat_currencies else 'circle'
    for i in range(len(G_ig.vs))
]

# Asignar etiquetas a las monedas fiat y a las criptomonedas en el top 5 de PageRank
vertex_labels = [
    G_ig.vs[i]['name'] if G_ig.vs[i]['name'] in aes_fiat_currencies or G_ig.vs[i]['name'] in emdes_fiat_currencies or i in top_5_cryptos else ''
    for i in range(len(G_ig.vs))
]

# Definir tamaños de las etiquetas basados en PageRank
min_font_size = 8
max_font_size = 18
vertex_label_sizes = [min_font_size + (pr / max_pagerank) ** 0.3 * (max_font_size - min_font_size) for pr in pagerank]

# Aplicar el layout de Fruchterman-Reingold
layout = G_ig.layout_fruchterman_reingold()

# Extraer las posiciones del layout y ajustar para aristas curvas
Xn = [layout[k][0] for k in range(len(G_ig.vs))]
Yn = [layout[k][1] for k in range(len(G_ig.vs))]
Xe = []
Ye = []
for edge in G_ig.es:
    x_mid = (layout[edge.source][0] + layout[edge.target][0]) / 2
    y_mid = (layout[edge.source][1] + layout[edge.target][1]) / 2
    Xe += [layout[edge.source][0], x_mid, layout[edge.target][0], None]
    Ye += [layout[edge.source][1], y_mid, layout[edge.target][1], None]

# Graficar usando Plotly
trace1 = go.Scatter(
    x=Xe,
    y=Ye,
    mode='lines',
    line=dict(color='rgb(240, 240, 240)', width=1),  # Líneas de color gris claro
    hoverinfo='none'
)

trace2 = go.Scatter(
    x=Xn,
    y=Yn,
    mode='markers+text',
    name='ntw',
    marker=dict(
        symbol=vertex_shapes,
        size=vertex_sizes, 
        color=vertex_colors,
        line=dict(width=0)  # Eliminar el borde de los nodos
    ),
    text=vertex_labels,
    textposition='top center',
    textfont=dict(color=label_colors, size=vertex_label_sizes),  # Usar tamaños de fuente basados en PageRank
    hoverinfo='text'
)

# Ajustar el layout del gráfico
layout_plot = go.Layout(
    font=dict(size=10),
    showlegend=False,
    autosize=False,
    width=500,
    height=350,
    paper_bgcolor='white',
    plot_bgcolor='white',
    xaxis=dict(showline=False, zeroline=False, showgrid=False, showticklabels=False),
    yaxis=dict(showline=False, zeroline=False, showgrid=False, showticklabels=False),
    margin=dict(l=0, r=0, b=0, t=0),
    hovermode='closest'
)

fig_f1 = go.Figure(data=[trace1, trace2], layout=layout_plot)

# Exportar el gráfico a HTML manteniendo la interactividad
fig_f1.write_html("fig_f1.html")


In [62]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Ordenar los datos de mayor a menor para el primer gráfico
crypto_count_per_fiat_sorted = crypto_count_per_fiat.sort_values(ascending=False)

# Crear la figura con 1 fila y 2 columnas
fig_f2 = make_subplots(rows=1, cols=2)

# Gráfico 1: Número de criptomonedas únicas por moneda fiat (ordenado)
for country in crypto_count_per_fiat_sorted.index:
    color = country_colors.get(country, ['#CCCCCC', '#999999'])[0]  # Mantener los colores originales
    fig_f2.add_trace(go.Bar(
        x=[country],  
        y=[crypto_count_per_fiat_sorted[country]],  
        marker_color=color,  
        name=country
    ), row=1, col=1)

# Definir colores para BTC, USDT y otras criptomonedas
crypto_colors = {
    'BTC': '#F7931A',   # Naranja para Bitcoin
    'USDT': '#26A17B',  # Verde para Tether
}

# Gráfico 2: Frecuencia única de las 15 principales criptomonedas en el último mes
for crypto in top_15_cryptos.index:
    color = crypto_colors.get(crypto, '#B0B0B0')  # Usar gris para criptomonedas que no son BTC o USDT
    fig_f2.add_trace(go.Bar(
        x=[crypto],
        y=[top_15_cryptos[crypto]],
        marker_color=color,
        name=crypto
    ), row=1, col=2)

# Ajustar el diseño final
fig_f2.update_layout(
    height=350, 
    width=500, 
    showlegend=False,  # Ocultar leyenda
    margin=dict(l=0, r=0, b=0, t=0),  # Margen mínimo
    plot_bgcolor='white',  # Fondo blanco
    paper_bgcolor='white',  # Fondo blanco del papel
    font=dict(
        family="Verdana, sans-serif",  # Usar Verdana como fuente
        color="#4D4D4D",  # Usar gris oscuro para todo el texto
        size=12  # Tamaño de la fuente
    ),
    xaxis=dict(
        tickfont=dict(color="#4D4D4D"),  # Gris oscuro para las etiquetas del eje X
        showline=False,
        zeroline=False,
        showgrid=False
    ),
    yaxis=dict(
        tickfont=dict(color="#4D4D4D"),  # Gris oscuro para las etiquetas del eje Y
        showline=False,
        zeroline=False,
        showgrid=False
    )
)

# Exportar el gráfico a HTML manteniendo la interactividad
fig_f2.write_html("fig_f2.html")


In [63]:
import pandas as pd
import plotly.graph_objects as go
import warnings
from tqdm.notebook import tqdm  # Para mostrar la barra de progreso

# Suprimir el SettingWithCopyWarning
warnings.simplefilter(action='ignore', category=pd.errors.SettingWithCopyWarning)

# Asegurar que 'timestamp' esté en formato datetime
final_df['timestamp'] = pd.to_datetime(final_df['timestamp'])

# Contar el número de pares para cada criptomoneda en todo el dataset
all_crypto_counts = final_df['crypto_currency'].value_counts()

# Identificar las 10 principales criptomonedas basadas en todo el dataset
top_10_cryptos = all_crypto_counts.nlargest(10).index.tolist()

# Definir categorías para el eje Y (top 10 criptos + 'Others')
categories = top_10_cryptos + ['Others']

# Extraer el mes del timestamp
final_df['month'] = final_df['timestamp'].dt.to_period('M')

# Extender los datos para incluir hasta 2024-08, incluso si no hay nuevas entradas
all_months = pd.period_range(final_df['month'].min(), '2024-08', freq='M')

# Lista de todas las monedas fiat presentes en el dataset
all_fiats = sorted(final_df['fiat_currency'].unique())  # Ordenar las monedas fiat alfabéticamente

# Inicializar una lista para almacenar todos los frames
frames = []

# Generar un frame para cada mes
for month in tqdm(all_months, desc="Generating frames"):
    # Filtrar los datos para el mes dado
    monthly_data = final_df[final_df['month'] == month].copy()

    # Agrupar las criptomonedas restantes en "Others"
    if not monthly_data.empty:
        monthly_data.loc[:, 'crypto_category'] = monthly_data['crypto_currency'].apply(
            lambda x: x if x in top_10_cryptos else 'Others'
        )

    # Inicializar una matriz vacía con ceros (sin pares)
    matrix = pd.DataFrame(0, index=categories, columns=all_fiats)

    # Llenar la matriz con 1 donde existan pares
    if not monthly_data.empty:
        for _, row in monthly_data.iterrows():
            matrix.loc[row['crypto_category'], row['fiat_currency']] = 1

    # Crear un frame para este mes
    frames.append(go.Frame(
        data=go.Heatmap(
            z=matrix.values,
            x=matrix.columns,
            y=matrix.index,
            colorscale=[[0, '#D3D3D3'], [1, '#4682B4']],  # Gris claro para sin par, azul acero para todos los pares
            showscale=False
        ),
        name=str(month)
    ))

# Graficar usando Plotly
fig_f3 = go.Figure(
    data=frames[0]['data'],  # Usar los datos del primer mes como punto de partida
    layout=go.Layout(
        xaxis_title="Fiat Currency",
        yaxis_title="Cryptocurrency",
        yaxis=dict(
            tickmode='array',
            tickvals=list(range(len(categories))),
            ticktext=categories,
            tickfont=dict(size=10),
            side='left'
        ),
        xaxis=dict(
            tickmode='array',
            tickvals=list(range(len(all_fiats))),
            ticktext=all_fiats  # Ordenado alfabéticamente
        ),
        template="plotly_white",
        autosize=False,
        width=500,
        height=350,
        margin=dict(l=0, r=0, b=0, t=0),  # Margen mínimo
        paper_bgcolor='white',  # Fondo blanco
        plot_bgcolor='white',   # Fondo blanco del área de trazado
        sliders=[{
            'currentvalue': {
                'prefix': 'Month: ',
                'font': {'size': 10}
            },
            'pad': {'b': 10},
            'len': 0.9,
            'x': 0.1,
            'y': -0.15,
            'steps': [{
                'args': [[str(month)], {
                    'frame': {'duration': 500, 'redraw': True},
                    'mode': 'immediate',
                    'transition': {'duration': 300}
                }],
                'label': str(month),
                'method': 'animate'
            } for month in all_months]
        }]
    ),
    frames=frames  # Agregar los frames a la figura
)

# Exportar el gráfico a HTML manteniendo la interactividad
fig_f3.write_html("fig_f3.html")


Generating frames:   0%|          | 0/59 [00:00<?, ?it/s]

In [64]:
import igraph as ig
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Definir el diccionario para acumular volúmenes
total_volume_dict = {}

# Calcular los volúmenes totales por nodo
for _, row in new_base.iterrows():
    asset = row['Asset']
    country = row['Country']
    volume = row['VolumeUSD']
    
    # Acumular volúmenes
    total_volume_dict[asset] = total_volume_dict.get(asset, 0) + volume
    total_volume_dict[country] = total_volume_dict.get(country, 0) + volume

# Determinar el volumen máximo
max_volume = max(total_volume_dict.values())

# Clasificación de monedas fiat en AEs y EMDEs
aes_currencies = ['USD', 'EUR', 'GBP', 'JPY', 'AUD', 'CZK']  # Economías Avanzadas
emdes_currencies = ['NGN', 'RUB', 'TRY', 'ZAR', 'UAH', 'BRL', 'ERN', 'PLN', 'RON', 'ARS', 'MXN']  # Mercados Emergentes

aes_color = '#AA322F'  # Rojo oscuro para AEs
emdes_color = '#6FA5E2'  # Azul pastel más oscuro para EMDEs
crypto_color = '#D3D3D3'  # Gris claro para criptomonedas

# Crear una figura con 4 subplots (2x2)
fig_f4 = make_subplots(rows=2, cols=2, vertical_spacing=0.1)

# Definir los años para cada subplot
years = [2021, 2022, 2023, 2024]
positions = [(1, 1), (1, 2), (2, 1), (2, 2)]

for year, pos in zip(years, positions):
    yearly_data = new_base[new_base['Year'] == year]
    vertices = set()
    edges = []
    weights = []
    
    for _, row in yearly_data.iterrows():
        asset = row['Asset']
        country = row['Country']
        volume = row['VolumeUSD']
        
        vertices.add(asset)
        vertices.add(country)
        edges.append((asset, country))
        weights.append(volume)
    
    vertices = list(vertices)
    G_ig = ig.Graph()
    G_ig.add_vertices(vertices)
    G_ig.add_edges(edges)
    G_ig.es['weight'] = weights
    
    layout = G_ig.layout('circle')
    Xn = [layout[k][0] for k in range(len(G_ig.vs))]
    Yn = [layout[k][1] for k in range(len(G_ig.vs))]
    Xe = []
    Ye = []
    for e in G_ig.es:
        Xe.extend([layout[e.source][0], layout[e.target][0], None])
        Ye.extend([layout[e.source][1], layout[e.target][1], None])
    
    vertex_sizes = [(total_volume_dict.get(v, 0) / max_volume) * 40 + 10 for v in G_ig.vs['name']]
    vertex_colors = [aes_color if v in aes_currencies else emdes_color if v in emdes_currencies else '#D3D3D3' for v in G_ig.vs['name']]
    
    # Agregar nodos al subplot correspondiente
    fig_f4.add_trace(go.Scatter(x=Xn, y=Yn,
                                mode='markers+text',
                                marker=dict(symbol='circle',
                                            size=vertex_sizes,
                                            color=vertex_colors,
                                            line=dict(color='black', width=0.5)),
                                text=G_ig.vs['name'],
                                textposition='top center',
                                textfont=dict(size=10),
                                hoverinfo='text'),  # Mantener interactividad
                     row=pos[0], col=pos[1])
    
    # Agregar aristas con grosor específico para cada traza
    for i, e in enumerate(G_ig.es):
        fig_f4.add_trace(go.Scatter(x=[layout[e.source][0], layout[e.target][0], None],
                                    y=[layout[e.source][1], layout[e.target][1], None],
                                    mode='lines',
                                    line=dict(width=(weights[i] / max(weights)) * 5, color='grey'),
                                    hoverinfo='none'),
                         row=pos[0], col=pos[1])

# Ajustar el diseño de la figura manteniendo la interactividad
fig_f4.update_layout(
    height=350,  # Ajustar a 350 px de alto
    width=500,   # Ajustar a 500 px de ancho
    showlegend=False,
    margin=dict(l=10, r=10, t=10, b=10),  # Márgenes mínimos
    paper_bgcolor='white',  # Fondo blanco
    plot_bgcolor='white',   # Fondo blanco del área de trazado
    xaxis=dict(showticklabels=False, zeroline=False),
    yaxis=dict(showticklabels=False, zeroline=False),
    hovermode='closest'  # Mantener interactividad
)

# Aplicar eliminación de escalas a todos los subplots
for i in range(1, 5):
    fig_f4.update_xaxes(showticklabels=False, row=(i+1)//2, col=(i-1)%2 + 1)
    fig_f4.update_yaxes(showticklabels=False, row=(i+1)//2, col=(i-1)%2 + 1)

# Exportar el gráfico a HTML manteniendo la interactividad
fig_f4.write_html("fig_f4.html")


In [65]:
from plotly.subplots import make_subplots

# Crear la figura con 1 fila y 2 columnas
fig_f5 = make_subplots(rows=1, cols=2, subplot_titles=("by Cryptocurrency", "by Country"))

# Agregar las trazas de los gráficos ya existentes a los subplots
for trace in fig_vol_cryptos['data']:
    fig_f5.add_trace(trace, row=1, col=1)

for trace in fig_vol_countries['data']:
    fig_f5.add_trace(trace, row=1, col=2)

# Actualizar el diseño para eliminar títulos, ajustar tamaño, y márgenes
fig_f5.update_traces(marker=dict(line=dict(width=0)), selector=dict(type='bar'))

# Ajustar el diseño para la figura final
fig_f5.update_layout(
    barmode='stack',
    height=350,  # Ajustar a 350 px de alto
    width=500,   # Ajustar a 500 px de ancho
    showlegend=True,
    margin=dict(l=10, r=10, t=10, b=10),  # Márgenes mínimos
    paper_bgcolor='white',  # Fondo blanco
    plot_bgcolor='white',   # Fondo blanco del área de trazado
    xaxis=dict(showline=False, zeroline=False, showgrid=False, showticklabels=True),
    yaxis=dict(showline=False, zeroline=False, showgrid=False, showticklabels=True),
)

# Exportar el gráfico a HTML manteniendo la interactividad
fig_f5.write_html("fig_f5.html")


In [66]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Crear los subplots uno al lado del otro con un tamaño más adecuado
fig_f6 = make_subplots(rows=1, cols=2, shared_yaxes=True, subplot_titles=("AEs", "EMDEs"))

# Definir colores para BTC, USDT y Others
colores = {
    'BTC': '#F7931A',   # Naranja para Bitcoin
    'USDT': '#26A17B',  # Verde para Tether
    'OTHERS': '#B0B0B0'  # Gris para otras criptomonedas
}

# Asegurar el orden de las barras: BTC (primero), USDT (segundo), Others (tercero)
order = ['BTC', 'USDT', 'OTHERS']

# Agregar trazas para AEs
for crypto in order:
    if crypto in aes_grouped['crypto_currency'].unique():
        df_crypto = aes_grouped[aes_grouped['crypto_currency'] == crypto]
        fig_f6.add_trace(go.Bar(
            x=df_crypto['timestamp'],
            y=df_crypto['volumeUSD'],
            name=crypto.upper(),
            marker_color=colores.get(crypto.upper(), '#000000'),
            showlegend=True
        ), row=1, col=1)

# Agregar trazas para EMDEs
for crypto in order:
    if crypto in emdes_grouped['crypto_currency'].unique():
        df_crypto = emdes_grouped[emdes_grouped['crypto_currency'] == crypto]
        fig_f6.add_trace(go.Bar(
            x=df_crypto['timestamp'],
            y=df_crypto['volumeUSD'],
            name=crypto.upper(),
            marker_color=colores.get(crypto.upper(), '#000000'),
            showlegend=False  # No mostrar leyenda dos veces
        ), row=1, col=2)

# Personalizar el diseño del gráfico para ajustarlo al tamaño deseado
fig_f6.update_layout(
    barmode='stack',
    height=350,  # Ajustar la altura del gráfico a 350 px
    width=500,   # Ajustar el ancho del gráfico a 500 px
    margin=dict(l=10, r=10, t=10, b=10),  # Márgenes mínimos
    paper_bgcolor='white',  # Fondo blanco
    plot_bgcolor='white',   # Fondo blanco del área de trazado
    showlegend=True,
    xaxis=dict(showline=False, zeroline=False, showgrid=False, showticklabels=True),
    yaxis=dict(showline=False, zeroline=False, showgrid=False, showticklabels=True),
)

# Exportar el gráfico a HTML manteniendo la interactividad
fig_f6.write_html("fig_f6.html")


In [67]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Filtrar los datos para incluir solo los registros de 2024
aes_grouped_2024 = aes_grouped[aes_grouped['timestamp'].dt.year == 2024]
emdes_grouped_2024 = emdes_grouped[emdes_grouped['timestamp'].dt.year == 2024]

# Sumarizar los volúmenes a nivel anual por criptomoneda
aes_annual = aes_grouped_2024.groupby('crypto_currency')['volumeUSD'].sum().reset_index()
emdes_annual = emdes_grouped_2024.groupby('crypto_currency')['volumeUSD'].sum().reset_index()

# Calcular el volumen total anual para cada tipo de economía
aes_total_annual = aes_annual['volumeUSD'].sum()
emdes_total_annual = emdes_annual['volumeUSD'].sum()

# Calcular los porcentajes de cada criptomoneda en el total anual
aes_annual['percentage'] = aes_annual['volumeUSD'] / aes_total_annual * 100
emdes_annual['percentage'] = emdes_annual['volumeUSD'] / emdes_total_annual * 100

# Crear los subplots uno al lado del otro con un tamaño más adecuado
fig_f7 = make_subplots(rows=1, cols=2, shared_yaxes=True, subplot_titles=("AEs", "EMDEs"))

# Definir colores para BTC, USDT y Others
colores = {
    'BTC': '#F7931A',   # Naranja para Bitcoin
    'USDT': '#26A17B',  # Verde para Tether
    'OTHERS': '#B0B0B0'  # Gris para otras criptomonedas
}

# Asegurar el orden de las barras: BTC (primero), USDT (segundo), Others (tercero)
order = ['BTC', 'USDT', 'OTHERS']

# Agregar trazas para AEs
for crypto in order:
    if crypto in aes_annual['crypto_currency'].unique():
        df_crypto = aes_annual[aes_annual['crypto_currency'] == crypto]
        fig_f7.add_trace(go.Bar(
            x=['AEs'],
            y=df_crypto['percentage'],
            name=crypto.upper(),
            marker_color=colores.get(crypto.upper(), '#000000'),
            showlegend=True
        ), row=1, col=1)

# Agregar trazas para EMDEs
for crypto in order:
    if crypto in emdes_annual['crypto_currency'].unique():
        df_crypto = emdes_annual[emdes_annual['crypto_currency'] == crypto]
        fig_f7.add_trace(go.Bar(
            x=['EMDEs'],
            y=df_crypto['percentage'],
            name=crypto.upper(),
            marker_color=colores.get(crypto.upper(), '#000000'),
            showlegend=False  # No mostrar leyenda dos veces
        ), row=1, col=2)

# Personalizar el diseño del gráfico para ajustarlo al tamaño deseado
fig_f7.update_layout(
    barmode='stack',
    height=350,  # Ajustar la altura del gráfico a 350 px
    width=500,   # Ajustar el ancho del gráfico a 500 px
    margin=dict(l=10, r=10, t=10, b=10),  # Márgenes mínimos
    paper_bgcolor='white',  # Fondo blanco
    plot_bgcolor='white',   # Fondo blanco del área de trazado
    showlegend=True,
    font=dict(
        family="Verdana, sans-serif",  # Cambiar la fuente a Verdana
        color="#4D4D4D",  # Gris oscuro para todo el texto
        size=12
    ),
    xaxis=dict(
        showline=False, 
        zeroline=False, 
        showgrid=False, 
        showticklabels=True,
        tickfont=dict(color="#4D4D4D")  # Cambiar el color de las etiquetas del eje X a gris oscuro
    ),
    yaxis=dict(
        showline=False, 
        zeroline=False, 
        showgrid=False, 
        showticklabels=True,
        tickfont=dict(color="#4D4D4D")  # Cambiar el color de las etiquetas del eje Y a gris oscuro
    ),
    legend=dict(
        font=dict(color="#4D4D4D"),  # Cambiar el color del texto de la leyenda a gris oscuro
    )
)

# Exportar el gráfico a HTML manteniendo la interactividad
fig_f7.write_html("fig_f7.html")


In [68]:
import os
import git
from kaggle_secrets import UserSecretsClient

# Retrieve GitHub token securely from Kaggle secrets
user_secrets = UserSecretsClient()
GITHUB_TOKEN = user_secrets.get_secret("GITHUB_TOKEN")

# Set up the repository URL using the secured token
REPO_URL = "https://{}@github.com/emigiupponi/CryptoFiatVisualizer.git".format(GITHUB_TOKEN)

# Clone the repository if not already done
if not os.path.exists('repo'):
    repo = git.Repo.clone_from(REPO_URL, 'repo')

repo = git.Repo('repo')

# Exportar los nuevos gráficos a HTML con tamaño ajustado
fig_f1.update_layout(width=500, height=350)
fig_f2.update_layout(width=500, height=350)
fig_f3.update_layout(width=500, height=350)
fig_f4.update_layout(width=500, height=350)
fig_f5.update_layout(width=500, height=350)
fig_f6.update_layout(width=500, height=350)
fig_f7.update_layout(width=500, height=350)

fig_f1.write_html("fig_f1.html", include_plotlyjs='cdn', full_html=False, config={'responsive': True})
fig_f2.write_html("fig_f2.html", include_plotlyjs='cdn', full_html=False, config={'responsive': True})
fig_f3.write_html("fig_f3.html", include_plotlyjs='cdn', full_html=False, config={'responsive': True})
fig_f4.write_html("fig_f4.html", include_plotlyjs='cdn', full_html=False, config={'responsive': True})
fig_f5.write_html("fig_f5.html", include_plotlyjs='cdn', full_html=False, config={'responsive': True})
fig_f6.write_html("fig_f6.html", include_plotlyjs='cdn', full_html=False, config={'responsive': True})
fig_f7.write_html("fig_f7.html", include_plotlyjs='cdn', full_html=False, config={'responsive': True})

# Move HTML files to the repo
copy_result = os.system('cp *.html repo/')
print(f"Copy result: {copy_result}")

# List files in the repo directory
print("Files in repo directory:")
print(os.listdir('repo'))

# Commit and push to GitHub
repo.index.add([
    'fig_f1.html',
    'fig_f2.html',
    'fig_f3.html',
    'fig_f4.html',
    'fig_f5.html',
    'fig_f6.html',
    'fig_f7.html'
])

commit_result = repo.index.commit("Add resized crypto fiat visualizations (f1 to f7)")
print(f"Commit result: {commit_result}")

push_result = repo.remote(name='origin').push()
print(f"Push result: {push_result}")


Copy result: 0
Files in repo directory:
['fig_vol_type_econ.html', '.git', 'fig_stacked_bar_crypto_volumes_2024.html', 'index.html', 'fig_heatmap_animated.html', 'fig_network_evolution.html', 'crypto_fiat_animation.html', 'crypto_fiat_animation_new.html', 'fig_f1.html', 'binance-volume.ipynb', 'fig_f5.html', 'fig_comparative_crypto_metrics.html', 'README.md', 'fig_f2.html', 'fig_f7.html', 'fig_comparative_crypto_volumes.html', 'fig_f3.html', 'fig_f4.html', 'fig_f6.html']
Commit result: 6f7fd2c15e09dd318230720cd5b12dd605a586d0
Push result: [<git.remote.PushInfo object at 0x7b6f9e6c6b60>]
